## Setup

In [1]:
import pandas as pd
import numpy as np
import altair as alt
import paretoset

alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [2]:
### A bit of an awkward solution for now
## Import resindential and industrial loads
loads_residential= pd.read_csv(
    'Data/LoadProfiles_SE_Residential.csv',
)

loads_to_use_residential= [
    'residential1',
    'residential2',
    'residential3',
    'residential4',
    'residential5'
]



loads_industrial= pd.read_csv(
    'Data/LoadProfiles_SE_Industrial.csv',
)

loads_to_use_industrial= [
    'industrial1',
    'industrial2',
]





## Create a common DataFrame for the loads
loads_selected= pd.merge(
    loads_residential[['Hour', 'residential1', 'residential2', 'residential3', 'residential4','residential5']],
    loads_industrial[['Hour', 'industrial1', 'industrial2']]
)

loads_to_read= [
    'residential1',
    'residential2',
    'residential3',
    'residential4',
    'residential5',
    'industrial1',
    'industrial2',
]





solar_multiples=    [0.5, 1, 1.5, 2, 2.5, 3, 3.5, 4, 4.5, 5]
bess_multiples=     [0.5, 1, 1.5, 2, 2.5, 3, 3.5, 4, 4.5, 5]
bess_capacities=    [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10]
optimise_for=       ['Price', 'CO_2_eq']





data_de=    pd.read_csv('Data/data_de.csv', sep= ';', index_col= False)
data_es=    pd.read_csv('Data/data_es.csv', sep= ';', index_col= False)
data_it=    pd.read_csv('Data/data_it.csv', sep= ';', index_col= False)
data_pl=    pd.read_csv('Data/data_pl.csv', sep= ';', index_col= False)
data_se=    pd.read_csv('Data/data_se.csv', sep= ';', index_col= False)
data_se1=   pd.read_csv('Data/data_se1.csv', sep= ';', index_col= False)
data_se2=   pd.read_csv('Data/data_se2.csv', sep= ';', index_col= False)
data_se3=   pd.read_csv('Data/data_se3.csv', sep= ';', index_col= False)
data_se4=   pd.read_csv('Data/data_se4.csv', sep= ';', index_col= False)

data_dict= {
    'DE': data_de,
    'ES': data_es,
    'IT': data_it,
    'PL': data_pl,
    'SE': data_se,
    'SE1': data_se1,
    'SE2': data_se2,
    'SE3': data_se3,
    'SE4': data_se4,
}

regions= [
    'DE',
    'ES',
    'IT',
    'PL',
    'SE',
    'SE1',
    'SE2',
    'SE3',
    'SE4',
]

### Auxiliary functions

In [3]:
def replace_value_in_column(df, column_name, old_value, new_value):
    df[column_name] = df[column_name].replace(old_value, new_value)
    return df

def remove_rows_with_specific_value(df, column_name, value):
    return df[df[column_name] != value]

def remove_rows_above_specific_value(df, column_name, value):
    return df[df[column_name] <= value]

def remove_rows_below_specific_value(df, column_name, value):
    return df[df[column_name] >= value]

def get_pareto_front(point, points):
    return np.any(np.all(points <= point, axis=1)) and np.any(np.all(points > point, axis=1))

In [4]:
def extract_pareto_front_curve(dataframe, region, load_source, kpi1, kpi2):
    '''
    Since my results are batch post-processed in a single DataFrame,
    the first step is to create a sub-DataFrame that is specified based on the input parameters region and load 
    '''
    
    specified_dataframe= dataframe[
        (dataframe['region'] == region)
        & (dataframe['load_source'] == load_source)
    ]
    specified_dataframe= specified_dataframe.reset_index(drop= True)

    '''
    Extracting the Pareto Front points,
    then merging them in the result DataFrame
    '''
    specified_dataframe_min= paretoset.paretoset(specified_dataframe[[kpi1, kpi2]].values, sense= ['min', 'min'])
    specified_dataframe_max= paretoset.paretoset(specified_dataframe[[kpi1, kpi2]].values, sense= ['min', 'max'])

    pareto_front_points= pd.merge(
        specified_dataframe.iloc[specified_dataframe_min],
        specified_dataframe.iloc[specified_dataframe_max],
        how= 'outer'
    )
    
    pareto_front_points['pareto_front']= f'{kpi1}-{kpi2}-{region}-{load_source}'

    return pareto_front_points

In [ ]:
def extract_pareto_front_isocurve(dataframe, region, load_source, variable, variable_value, kpi1, kpi2):
    '''
    Since my results are batch post-processed in a single DataFrame,
    the first step is to create a sub-DataFrame that is specified based on the input parameters region and load 
    '''

    specified_dataframe= dataframe[
        (dataframe['region'] == region)
        & (dataframe['load_source'] == load_source)
        & (dataframe[variable] == variable_value)
    ]
    specified_dataframe= specified_dataframe.reset_index(drop= True)

    '''
    Extracting the Pareto Front points,
    then merging them in the result DataFrame
    '''
    specified_dataframe_min= paretoset.paretoset(specified_dataframe[[kpi1, kpi2]].values, sense= ['min', 'min'])
    specified_dataframe_max= paretoset.paretoset(specified_dataframe[[kpi1, kpi2]].values, sense= ['min', 'max'])

    pareto_front_points= pd.merge(
        specified_dataframe.iloc[specified_dataframe_min],
        specified_dataframe.iloc[specified_dataframe_max],
        how= 'outer'
    )
    
    pareto_front_points['pareto_front']= f'{kpi1}-{kpi2}-{region}-{load_source}'

    return pareto_front_points


def iterate_and_extract_pareto_isocurves():
    
    
    return

### Load the post-processed results & Dropping duplicated rows

In [5]:
results_econ=   pd.read_csv('RESULTS/Results_econ.csv')
results_env=    pd.read_csv('RESULTS/Results_env.csv')

In [6]:
results_econ=   results_econ.drop_duplicates(
    subset= [
        'P_PV',
        'E_BESS',
        'load_source',
        'region'
    ]
)
results_env=    results_env.drop_duplicates(
    subset= [
        'P_PV',
        'E_BESS',
        'load_source',
        'region'
    ]
)

In [8]:
results_econ.groupby(['region']).count()

P_PV  P_BESS  E_BESS  T_BESS  pv2load  pv2bess  pv2curtail  pv2grid  \
region                                                                        
DE      1185    1185    1185    1185     1185     1185        1185     1185   
ES      1301    1301    1301    1301     1301     1301        1301     1301   
IT      1544    1544    1544    1544     1544     1544        1544     1544   
PL      1386    1386    1386    1386     1386     1386        1386     1386   
SE      1190    1190    1190    1190     1190     1190        1190     1190   
SE1     1190    1190    1190    1190     1190     1190        1190     1190   
SE2     1190    1190    1190    1190     1190     1190        1190     1190   
SE3     1433    1433    1433    1433     1433     1433        1433     1433   
SE4     1190    1190    1190    1190     1190     1190        1190     1190   

        bess2load  bess2grid  ...  co2burden_load  co2burden_bess  \
region                        ...                                   
DE           1185       1185  ...            1185            1185   
ES           1301       1301  ...            1301            1301   
IT           1544       1544  ...            1544            1544   
PL           1386       1386  ...            1386            1386   
SE           1190       1190  ...            1190            1190   
SE1          1190       1190  ...            1190            1190   
SE2          1190       1190  ...            1190            1190   
SE3          1433       1433  ...            1433            1433   
SE4          1190       1190  ...            1190            1190   

        co2abatement  co2abatement_pv  co2abatement_bess  cycles  \
region                                                             
DE              1185             1185               1185    1185   
ES              1301             1301               1301    1301   
IT              1544             1544               1544    1544   
PL              1386             1386               1386    1386   
SE              1190             1190               1190    1190   
SE1             1190             1190               1190    1190   
SE2             1190             1190               1190    1190   
SE3             1433             1433               1433    1433   
SE4             1190             1190               1190    1190   

        self_sufficiency  ress  self_consumption  load_source  
region                                                         
DE                  1185  1185              1185         1185  
ES                  1301  1301              1301         1301  
IT                  1544  1544              1544         1544  
PL                  1386  1386              1386         1386  
SE                  1190  1190              1190         1190  
SE1                 1190  1190              1190         1190  
SE2                 1190  1190              1190         1190  
SE3                 1433  1433              1433         1433  
SE4                 1190  1190              1190         1190  

[9 rows x 50 columns]

In [9]:
results_econ.groupby(['load_source']).count()

P_PV  P_BESS  E_BESS  T_BESS  pv2load  pv2bess  pv2curtail  \
load_source                                                                
industrial1   2987    2987    2987    2987     2987     2987        2987   
industrial2   2955    2955    2955    2955     2955     2955        2955   
residential1  1143    1143    1143    1143     1143     1143        1143   
residential2  1143    1143    1143    1143     1143     1143        1143   
residential3   884     884     884     884      884      884         884   
residential4  1613    1613    1613    1613     1613     1613        1613   
residential5   884     884     884     884      884      884         884   

              pv2grid  bess2load  bess2grid  ...  co2burden_load  \
load_source                                  ...                   
industrial1      2987       2987       2987  ...            2987   
industrial2      2955       2955       2955  ...            2955   
residential1     1143       1143       1143  ...            1143   
residential2     1143       1143       1143  ...            1143   
residential3      884        884        884  ...             884   
residential4     1613       1613       1613  ...            1613   
residential5      884        884        884  ...             884   

              co2burden_bess  co2abatement  co2abatement_pv  \
load_source                                                   
industrial1             2987          2987             2987   
industrial2             2955          2955             2955   
residential1            1143          1143             1143   
residential2            1143          1143             1143   
residential3             884           884              884   
residential4            1613          1613             1613   
residential5             884           884              884   

              co2abatement_bess  cycles  self_sufficiency  ress  \
load_source                                                       
industrial1                2987    2987              2987  2987   
industrial2                2955    2955              2955  2955   
residential1               1143    1143              1143  1143   
residential2               1143    1143              1143  1143   
residential3                884     884               884   884   
residential4               1613    1613              1613  1613   
residential5                884     884               884   884   

              self_consumption  region  
load_source                             
industrial1               2987    2987  
industrial2               2955    2955  
residential1              1143    1143  
residential2              1143    1143  
residential3               884     884  
residential4              1613    1613  
residential5               884     884  

[7 rows x 50 columns]

## Pareto fronts

### Splitting datasets

In [10]:
compare_paretos_regions_econ_lcoeinvestor= pd.concat(
    [
        extract_pareto_front_curve(results_econ, 'DE', 'res5', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_econ, 'ES', 'res5', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_econ, 'IT', 'res5', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_econ, 'PL', 'res5', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_econ, 'SE', 'res5', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_econ, 'SE1', 'res5', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_econ, 'SE2', 'res5', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_econ, 'SE3', 'res5', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_econ, 'SE4', 'res5', 'lcoe_investor', 'ress')
    ]
)

compare_paretos_regions_econ_lco2investor= pd.concat(
    [
        extract_pareto_front_curve(results_econ, 'DE', 'res5', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_econ, 'ES', 'res5', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_econ, 'IT', 'res5', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_econ, 'PL', 'res5', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_econ, 'SE', 'res5', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_econ, 'SE1', 'res5', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_econ, 'SE2', 'res5', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_econ, 'SE3', 'res5', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_econ, 'SE4', 'res5', 'lco2_investor', 'ress')
    ]
)

compare_paretos_regions_econ_lcoeenduser= pd.concat(
    [
        extract_pareto_front_curve(results_econ, 'DE', 'res5', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_econ, 'ES', 'res5', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_econ, 'IT', 'res5', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_econ, 'PL', 'res5', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_econ, 'SE', 'res5', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_econ, 'SE1', 'res5', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_econ, 'SE2', 'res5', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_econ, 'SE3', 'res5', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_econ, 'SE4', 'res5', 'lcoe_enduser', 'ress')
    ]
)

compare_paretos_regions_econ_lco2enduser= pd.concat(
    [
        extract_pareto_front_curve(results_econ, 'DE', 'res5', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_econ, 'ES', 'res5', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_econ, 'IT', 'res5', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_econ, 'PL', 'res5', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_econ, 'SE', 'res5', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_econ, 'SE1', 'res5', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_econ, 'SE2', 'res5', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_econ, 'SE3', 'res5', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_econ, 'SE4', 'res5', 'lco2_enduser', 'ress')
    ]
)



compare_paretos_regions_env_lcoeinvestor= pd.concat(
    [
        extract_pareto_front_curve(results_env, 'DE', 'res5', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_env, 'ES', 'res5', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_env, 'IT', 'res5', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_env, 'PL', 'res5', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_env, 'SE', 'res5', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_env, 'SE1', 'res5', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_env, 'SE2', 'res5', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_env, 'SE3', 'res5', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_env, 'SE4', 'res5', 'lcoe_investor', 'ress')
    ]
)

compare_paretos_regions_env_lco2investor= pd.concat(
    [
        extract_pareto_front_curve(results_env, 'DE', 'res5', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_env, 'ES', 'res5', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_env, 'IT', 'res5', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_env, 'PL', 'res5', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_env, 'SE', 'res5', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_env, 'SE1', 'res5', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_env, 'SE2', 'res5', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_env, 'SE3', 'res5', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_env, 'SE4', 'res5', 'lco2_investor', 'ress')
    ]
)

compare_paretos_regions_env_lcoeenduser= pd.concat(
    [
        extract_pareto_front_curve(results_env, 'DE', 'res5', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_env, 'ES', 'res5', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_env, 'IT', 'res5', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_env, 'PL', 'res5', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_env, 'SE', 'res5', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_env, 'SE1', 'res5', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_env, 'SE2', 'res5', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_env, 'SE3', 'res5', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_env, 'SE4', 'res5', 'lcoe_enduser', 'ress')
    ]
)

compare_paretos_regions_env_lco2enduser= pd.concat(
    [
        extract_pareto_front_curve(results_env, 'DE', 'res5', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_env, 'ES', 'res5', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_env, 'IT', 'res5', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_env, 'PL', 'res5', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_env, 'SE', 'res5', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_env, 'SE1', 'res5', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_env, 'SE2', 'res5', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_env, 'SE3', 'res5', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_env, 'SE4', 'res5', 'lco2_enduser', 'ress')
    ]
)

In [11]:
results_econ_italy=     results_econ[
    (results_econ['region'] == 'IT')
]
results_env_italy=      results_env[
    (results_env['region'] == 'IT')
]
results_econ_poland=    results_econ[
    (results_econ['region'] == 'PL')
]
results_env_poland=     results_env[
    (results_env['region'] == 'PL')
]
results_econ_sweden=    results_econ[
    (results_econ['region'] == 'SE')
]
results_env_sweden=     results_env[
    (results_env['region'] == 'SE')
]
results_econ_germany=   results_econ[
    (results_econ['region'] == 'DE')
]
results_env_germany=    results_env[
    (results_env['region'] == 'DE')
]
results_econ_spain=     results_econ[
    (results_econ['region'] == 'ES')
]
results_env_spain=      results_env[
    (results_env['region'] == 'ES')
]
results_econ_se1=    results_econ[
    (results_econ['region'] == 'SE1')
]
results_env_se1=     results_env[
    (results_env['region'] == 'SE1')
]
results_econ_se2=     results_econ[
    (results_econ['region'] == 'SE2')
]
results_env_se2=      results_env[
    (results_env['region'] == 'SE2')
]
results_econ_se3=    results_econ[
    (results_econ['region'] == 'SE3')
]
results_env_se3=     results_env[
    (results_env['region'] == 'SE3')
]
results_econ_se4=    results_econ[
    (results_econ['region'] == 'SE4')
]
results_env_se4=     results_env[
    (results_env['region'] == 'SE4')
]





results_econ_italy_industrial1=     results_econ[
    (results_econ['region'] == 'IT')
    & (results_econ['load_source'] == 'industrial1')
]
results_econ_italy_industrial2=     results_econ[
    (results_econ['region'] == 'IT')
    & (results_econ['load_source'] == 'industrial2')
]
results_econ_italy_residential4=     results_econ[
    (results_econ['region'] == 'IT')
    & (results_econ['load_source'] == 'residential4')
]
results_env_italy_industrial1=      results_env[
    (results_env['region'] == 'IT')
    & (results_env['load_source'] == 'industrial1')
]
results_env_italy_industrial2=      results_env[
    (results_env['region'] == 'IT')
    & (results_env['load_source'] == 'industrial2')
]
results_env_italy_residential4=      results_env[
    (results_env['region'] == 'IT')
    & (results_env['load_source'] == 'residential4')
]
results_econ_poland_industrial1=    results_econ[
    (results_econ['region'] == 'PL')
    & (results_econ['load_source'] == 'industrial1')
]
results_econ_poland_industrial2=    results_econ[
    (results_econ['region'] == 'PL')
    & (results_econ['load_source'] == 'industrial2')
]
results_econ_poland_residential4=    results_econ[
    (results_econ['region'] == 'PL')
    & (results_econ['load_source'] == 'residential4')
]
results_env_poland_industrial1=     results_env[
    (results_env['region'] == 'PL')
    & (results_env['load_source'] == 'industrial1')
]
results_env_poland_industrial2=     results_env[
    (results_env['region'] == 'PL')
    & (results_env['load_source'] == 'industrial2')
]
results_env_poland_residential4=     results_env[
    (results_env['region'] == 'PL')
    & (results_env['load_source'] == 'residential4')
]
results_econ_sweden_industrial1=    results_econ[
    (results_econ['region'] == 'SE3')
    & (results_econ['load_source'] == 'industrial1')
]
results_econ_sweden_industrial2=    results_econ[
    (results_econ['region'] == 'SE3')
    & (results_econ['load_source'] == 'industrial2')
]
results_econ_sweden_residential4=    results_econ[
    (results_econ['region'] == 'SE3')
    & (results_econ['load_source'] == 'residential4')
]
results_env_sweden_industrial1=     results_env[
    (results_env['region'] == 'SE3')
    & (results_env['load_source'] == 'industrial1')
]
results_env_sweden_industrial2=     results_env[
    (results_env['region'] == 'SE3')
    & (results_env['load_source'] == 'industrial2')
]
results_env_sweden_residential4=     results_env[
    (results_env['region'] == 'SE3')
    & (results_env['load_source'] == 'residential4')
]

In [12]:
paretos_italy_econ_lcoe_investor=    pd.concat(
    [
        extract_pareto_front_curve(results_econ_italy, 'IT', 'industrial1', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_econ_italy, 'IT', 'industrial2', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_econ_italy, 'IT', 'residential4', 'lcoe_investor', 'ress'),
    ]
)
paretos_italy_env_lcoe_investor=    pd.concat(
    [
        extract_pareto_front_curve(results_env_italy, 'IT', 'industrial1', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_env_italy, 'IT', 'industrial2', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_env_italy, 'IT', 'residential4', 'lcoe_investor', 'ress'),
    ]
)

paretos_italy_econ_lco2_investor=    pd.concat(
    [
        extract_pareto_front_curve(results_econ_italy, 'IT', 'industrial1', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_econ_italy, 'IT', 'industrial2', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_econ_italy, 'IT', 'residential4', 'lco2_investor', 'ress'),
    ]
)
paretos_italy_env_lco2_investor=    pd.concat(
    [
        extract_pareto_front_curve(results_env_italy, 'IT', 'industrial1', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_env_italy, 'IT', 'industrial2', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_env_italy, 'IT', 'residential4', 'lco2_investor', 'ress'),
    ]
)



paretos_italy_econ_lcoe_enduser=    pd.concat(
    [
        extract_pareto_front_curve(results_econ_italy, 'IT', 'industrial1', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_econ_italy, 'IT', 'industrial2', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_econ_italy, 'IT', 'residential4', 'lcoe_enduser', 'ress'),
    ]
)
paretos_italy_env_lcoe_enduser=    pd.concat(
    [
        extract_pareto_front_curve(results_env_italy, 'IT', 'industrial1', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_env_italy, 'IT', 'industrial2', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_env_italy, 'IT', 'residential4', 'lcoe_enduser', 'ress'),
    ]
)

paretos_italy_econ_lco2_enduser=    pd.concat(
    [
        extract_pareto_front_curve(results_econ_italy, 'IT', 'industrial1', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_econ_italy, 'IT', 'industrial2', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_econ_italy, 'IT', 'residential4', 'lco2_enduser', 'ress'),
    ]
)
paretos_italy_env_lco2_enduser=    pd.concat(
    [
        extract_pareto_front_curve(results_env_italy, 'IT', 'industrial1', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_env_italy, 'IT', 'industrial2', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_env_italy, 'IT', 'residential4', 'lco2_enduser', 'ress'),
    ]
)

In [13]:
paretos_poland_econ_lcoe_investor=    pd.concat(
    [
        extract_pareto_front_curve(results_econ_poland, 'PL', 'industrial1', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_econ_poland, 'PL', 'industrial2', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_econ_poland, 'PL', 'residential4', 'lcoe_investor', 'ress'),
    ]
)
paretos_poland_env_lcoe_investor=    pd.concat(
    [
        extract_pareto_front_curve(results_env_poland, 'PL', 'industrial1', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_env_poland, 'PL', 'industrial2', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_env_poland, 'PL', 'residential4', 'lcoe_investor', 'ress'),
    ]
)

paretos_poland_econ_lco2_investor=    pd.concat(
    [
        extract_pareto_front_curve(results_econ_poland, 'PL', 'industrial1', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_econ_poland, 'PL', 'industrial2', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_econ_poland, 'PL', 'residential4', 'lco2_investor', 'ress'),
    ]
)
paretos_poland_env_lco2_investor=    pd.concat(
    [
        extract_pareto_front_curve(results_env_poland, 'PL', 'industrial1', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_env_poland, 'PL', 'industrial2', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_env_poland, 'PL', 'residential4', 'lco2_investor', 'ress'),
    ]
)



paretos_poland_econ_lcoe_enduser=    pd.concat(
    [
        extract_pareto_front_curve(results_econ_poland, 'PL', 'industrial1', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_econ_poland, 'PL', 'industrial2', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_econ_poland, 'PL', 'residential4', 'lcoe_enduser', 'ress'),
    ]
)
paretos_poland_env_lcoe_enduser=    pd.concat(
    [
        extract_pareto_front_curve(results_env_poland, 'PL', 'industrial1', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_env_poland, 'PL', 'industrial2', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_env_poland, 'PL', 'residential4', 'lcoe_enduser', 'ress'),
    ]
)

paretos_poland_econ_lco2_enduser=    pd.concat(
    [
        extract_pareto_front_curve(results_econ_poland, 'PL', 'industrial1', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_econ_poland, 'PL', 'industrial2', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_econ_poland, 'PL', 'residential4', 'lco2_enduser', 'ress'),
    ]
)
paretos_poland_env_lco2_enduser=    pd.concat(
    [
        extract_pareto_front_curve(results_env_poland, 'PL', 'industrial1', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_env_poland, 'PL', 'industrial2', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_env_poland, 'PL', 'residential4', 'lco2_enduser', 'ress'),
    ]
)

In [14]:
paretos_sweden_econ_lcoe_investor=    pd.concat(
    [
        extract_pareto_front_curve(results_econ_sweden, 'SE', 'industrial1', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_econ_sweden, 'SE', 'industrial2', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_econ_sweden, 'SE', 'residential4', 'lcoe_investor', 'ress'),
    ]
)
paretos_sweden_env_lcoe_investor=    pd.concat(
    [
        extract_pareto_front_curve(results_env_sweden, 'SE', 'industrial1', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_env_sweden, 'SE', 'industrial2', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_env_sweden, 'SE', 'residential4', 'lcoe_investor', 'ress'),
    ]
)

paretos_sweden_econ_lco2_investor=    pd.concat(
    [
        extract_pareto_front_curve(results_econ_sweden, 'SE', 'industrial1', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_econ_sweden, 'SE', 'industrial2', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_econ_sweden, 'SE', 'residential4', 'lco2_investor', 'ress'),
    ]
)
paretos_sweden_env_lco2_investor=    pd.concat(
    [
        extract_pareto_front_curve(results_env_sweden, 'SE', 'industrial1', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_env_sweden, 'SE', 'industrial2', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_env_sweden, 'SE', 'residential4', 'lco2_investor', 'ress'),
    ]
)



paretos_sweden_econ_lcoe_enduser=    pd.concat(
    [
        extract_pareto_front_curve(results_econ_sweden, 'SE', 'industrial1', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_econ_sweden, 'SE', 'industrial2', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_econ_sweden, 'SE', 'residential4', 'lcoe_enduser', 'ress'),
    ]
)
paretos_sweden_env_lcoe_enduser=    pd.concat(
    [
        extract_pareto_front_curve(results_env_sweden, 'SE', 'industrial1', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_env_sweden, 'SE', 'industrial2', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_env_sweden, 'SE', 'residential4', 'lcoe_enduser', 'ress'),
    ]
)

paretos_sweden_econ_lco2_enduser=    pd.concat(
    [
        extract_pareto_front_curve(results_econ_sweden, 'SE', 'industrial1', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_econ_sweden, 'SE', 'industrial2', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_econ_sweden, 'SE', 'residential4', 'lco2_enduser', 'ress'),
    ]
)
paretos_sweden_env_lco2_enduser=    pd.concat(
    [
        extract_pareto_front_curve(results_env_sweden, 'SE', 'industrial1', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_env_sweden, 'SE', 'industrial2', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_env_sweden, 'SE', 'residential4', 'lco2_enduser', 'ress'),
    ]
)

In [15]:
paretos_residential4_econ_lcoe_investor=    pd.concat(
    [
        extract_pareto_front_curve(results_econ_italy_residential4, 'IT', 'residential4', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_econ_poland_residential4, 'PL', 'residential4', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_econ_sweden_residential4, 'SE3', 'residential4', 'lcoe_investor', 'ress'),
    ]
)
paretos_industrial1_econ_lcoe_investor=     pd.concat(
    [
        extract_pareto_front_curve(results_econ_italy_industrial1, 'IT', 'industrial1', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_econ_poland_industrial1, 'PL', 'industrial1', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_econ_sweden_industrial1, 'SE3', 'industrial1', 'lcoe_investor', 'ress'),
    ]
)
paretos_industrial2_econ_lcoe_investor=     pd.concat(
    [
        extract_pareto_front_curve(results_econ_italy_industrial2, 'IT', 'industrial2', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_econ_poland_industrial2, 'PL', 'industrial2', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_econ_sweden_industrial2, 'SE3', 'industrial2', 'lcoe_investor', 'ress'),
    ]
)
paretos_residential4_env_lcoe_investor=     pd.concat(
    [
        extract_pareto_front_curve(results_env_italy_residential4, 'IT', 'residential4', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_env_poland_residential4, 'PL', 'residential4', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_env_sweden_residential4, 'SE3', 'residential4', 'lcoe_investor', 'ress'),
    ]
)
paretos_industrial1_env_lcoe_investor=      pd.concat(
    [
        extract_pareto_front_curve(results_env_italy_industrial1, 'IT', 'industrial1', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_env_poland_industrial1, 'PL', 'industrial1', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_env_sweden_industrial1, 'SE3', 'industrial1', 'lcoe_investor', 'ress'),
    ]
)
paretos_industrial2_env_lcoe_investor=      pd.concat(
    [
        extract_pareto_front_curve(results_env_italy_industrial2, 'IT', 'industrial2', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_env_poland_industrial2, 'PL', 'industrial2', 'lcoe_investor', 'ress'),
        extract_pareto_front_curve(results_env_sweden_industrial2, 'SE3', 'industrial2', 'lcoe_investor', 'ress'),
    ]
)

paretos_residential4_econ_lcoe_enduser=    pd.concat(
    [
        extract_pareto_front_curve(results_econ_italy_residential4, 'IT', 'residential4', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_econ_poland_residential4, 'PL', 'residential4', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_econ_sweden_residential4, 'SE3', 'residential4', 'lcoe_enduser', 'ress'),
    ]
)
paretos_industrial1_econ_lcoe_enduser=    pd.concat(
    [
        extract_pareto_front_curve(results_econ_italy_industrial1, 'IT', 'industrial1', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_econ_poland_industrial1, 'PL', 'industrial1', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_econ_sweden_industrial1, 'SE3', 'industrial1', 'lcoe_enduser', 'ress'),
    ]
)
paretos_industrial2_econ_lcoe_enduser=    pd.concat(
    [
        extract_pareto_front_curve(results_econ_italy_industrial2, 'IT', 'industrial2', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_econ_poland_industrial2, 'PL', 'industrial2', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_econ_sweden_industrial2, 'SE3', 'industrial2', 'lcoe_enduser', 'ress'),
    ]
)
paretos_residential4_env_lcoe_enduser=    pd.concat(
    [
        extract_pareto_front_curve(results_env_italy_residential4, 'IT', 'residential4', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_env_poland_residential4, 'PL', 'residential4', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_env_sweden_residential4, 'SE3', 'residential4', 'lcoe_enduser', 'ress'),
    ]
)
paretos_industrial1_env_lcoe_enduser=    pd.concat(
    [
        extract_pareto_front_curve(results_env_italy_industrial1, 'IT', 'industrial1', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_env_poland_industrial1, 'PL', 'industrial1', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_env_sweden_industrial1, 'SE3', 'industrial1', 'lcoe_enduser', 'ress'),
    ]
)
paretos_industrial2_env_lcoe_enduser=    pd.concat(
    [
        extract_pareto_front_curve(results_env_italy_industrial2, 'IT', 'industrial2', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_env_poland_industrial2, 'PL', 'industrial2', 'lcoe_enduser', 'ress'),
        extract_pareto_front_curve(results_env_sweden_industrial2, 'SE3', 'industrial2', 'lcoe_enduser', 'ress'),
    ]
)



paretos_residential4_econ_lco2_investor=    pd.concat(
    [
        extract_pareto_front_curve(results_econ_italy_residential4, 'IT', 'residential4', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_econ_poland_residential4, 'PL', 'residential4', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_econ_sweden_residential4, 'SE3', 'residential4', 'lco2_investor', 'ress'),
    ]
)
paretos_industrial1_econ_lco2_investor=     pd.concat(
    [
        extract_pareto_front_curve(results_econ_italy_industrial1, 'IT', 'industrial1', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_econ_poland_industrial1, 'PL', 'industrial1', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_econ_sweden_industrial1, 'SE3', 'industrial1', 'lco2_investor', 'ress'),
    ]
)
paretos_industrial2_econ_lco2_investor=     pd.concat(
    [
        extract_pareto_front_curve(results_econ_italy_industrial2, 'IT', 'industrial2', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_econ_poland_industrial2, 'PL', 'industrial2', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_econ_sweden_industrial2, 'SE3', 'industrial2', 'lco2_investor', 'ress'),
    ]
)
paretos_residential4_env_lco2_investor=     pd.concat(
    [
        extract_pareto_front_curve(results_env_italy_residential4, 'IT', 'residential4', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_env_poland_residential4, 'PL', 'residential4', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_env_sweden_residential4, 'SE3', 'residential4', 'lco2_investor', 'ress'),
    ]
)
paretos_industrial1_env_lco2_investor=      pd.concat(
    [
        extract_pareto_front_curve(results_env_italy_industrial1, 'IT', 'industrial1', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_env_poland_industrial1, 'PL', 'industrial1', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_env_sweden_industrial1, 'SE3', 'industrial1', 'lco2_investor', 'ress'),
    ]
)
paretos_industrial2_env_lco2_investor=      pd.concat(
    [
        extract_pareto_front_curve(results_env_italy_industrial2, 'IT', 'industrial2', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_env_poland_industrial2, 'PL', 'industrial2', 'lco2_investor', 'ress'),
        extract_pareto_front_curve(results_env_sweden_industrial2, 'SE3', 'industrial2', 'lco2_investor', 'ress'),
    ]
)

paretos_residential4_econ_lco2_enduser=    pd.concat(
    [
        extract_pareto_front_curve(results_econ_italy_residential4, 'IT', 'residential4', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_econ_poland_residential4, 'PL', 'residential4', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_econ_sweden_residential4, 'SE3', 'residential4', 'lco2_enduser', 'ress'),
    ]
)
paretos_industrial1_econ_lco2_enduser=    pd.concat(
    [
        extract_pareto_front_curve(results_econ_italy_industrial1, 'IT', 'industrial1', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_econ_poland_industrial1, 'PL', 'industrial1', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_econ_sweden_industrial1, 'SE3', 'industrial1', 'lco2_enduser', 'ress'),
    ]
)
paretos_industrial2_econ_lco2_enduser=    pd.concat(
    [
        extract_pareto_front_curve(results_econ_italy_industrial2, 'IT', 'industrial2', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_econ_poland_industrial2, 'PL', 'industrial2', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_econ_sweden_industrial2, 'SE3', 'industrial2', 'lco2_enduser', 'ress'),
    ]
)
paretos_residential4_env_lco2_enduser=    pd.concat(
    [
        extract_pareto_front_curve(results_env_italy_residential4, 'IT', 'residential4', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_env_poland_residential4, 'PL', 'residential4', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_env_sweden_residential4, 'SE3', 'residential4', 'lco2_enduser', 'ress'),
    ]
)
paretos_industrial1_env_lco2_enduser=    pd.concat(
    [
        extract_pareto_front_curve(results_env_italy_industrial1, 'IT', 'industrial1', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_env_poland_industrial1, 'PL', 'industrial1', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_env_sweden_industrial1, 'SE3', 'industrial1', 'lco2_enduser', 'ress'),
    ]
)
paretos_industrial2_env_lco2_enduser=    pd.concat(
    [
        extract_pareto_front_curve(results_env_italy_industrial2, 'IT', 'industrial2', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_env_poland_industrial2, 'PL', 'industrial2', 'lco2_enduser', 'ress'),
        extract_pareto_front_curve(results_env_sweden_industrial2, 'SE3', 'industrial2', 'lco2_enduser', 'ress'),
    ]
)

___
### Paretos by Region

In [16]:
alt.vconcat(
    alt.hconcat(
        alt.Chart(
            paretos_italy_econ_lcoe_investor,
            title= 'Italy - LCOE Investor'
        ).mark_line(
            size= 3,
            clip= True
        ).encode(
            x= alt.X('ress:Q').scale(domain= (0, 90)),
            y= alt.Y('lcoe_investor:Q').scale(domain= (0, 0.12)),
            color= alt.Color('load_source:N'),
            tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS'])
        ),
        alt.Chart(
            paretos_poland_econ_lcoe_investor,
            title= 'Poland - LCOE Investor'
        ).mark_line(
            size= 3,
            clip= True
        ).encode(
            x= alt.X('ress:Q').scale(domain= (0, 90)),
            y= alt.Y('lcoe_investor:Q').scale(domain= (0, 0.12)),
            color= alt.Color('load_source:N'),
            tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS'])
        ),
        alt.Chart(
            paretos_sweden_econ_lcoe_investor,
            title= 'Sweden - LCOE Investor'
        ).mark_line(
            size= 3,
            clip= True
        ).encode(
            x= alt.X('ress:Q').scale(domain= (0, 90)),
            y= alt.Y('lcoe_investor:Q').scale(domain= (0, 0.12)),
            color= alt.Color('load_source:N'),
            tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS'])
        )
    ),
    alt.hconcat(
        alt.Chart(
            paretos_italy_econ_lcoe_enduser,
            title= 'Italy - LCOE End User'
        ).mark_line(
            size= 3,
            clip= True
        ).encode(
            x= alt.X('ress:Q').scale(domain= (0, 90)),
            y= alt.Y('lcoe_enduser:Q').scale(domain= (0, 0.12)),
            color= alt.Color('load_source:N'),
            tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS'])
        ),
        alt.Chart(
            paretos_poland_econ_lcoe_enduser,
            title= 'Poland - LCOE End User'
        ).mark_line(
            size= 3,
            clip= True
        ).encode(
            x= alt.X('ress:Q').scale(domain= (0, 90)),
            y= alt.Y('lcoe_enduser:Q').scale(domain= (0, 0.12)),
            color= alt.Color('load_source:N'),
            tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS'])
        ),
        alt.Chart(
            paretos_sweden_econ_lcoe_enduser,
            title= 'Sweden - LCOE End User'
        ).mark_line(
            size= 3,
            clip= True
        ).encode(
            x= alt.X('ress:Q').scale(domain= (0, 90)),
            y= alt.Y('lcoe_enduser:Q').scale(domain= (0, 0.12)),
            color= alt.Color('load_source:N'),
            tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS'])
        )
    )
)

alt.VConcatChart(...)

In [17]:
alt.vconcat(
    alt.hconcat(
        alt.Chart(
            paretos_italy_env_lco2_investor,
            title= 'Italy - LCO2eq Investor'
        ).mark_line(
            size= 3,
            clip= True
        ).encode(
            x= alt.X('ress:Q').scale(domain= (0, 90)),
            y= alt.Y('lco2_investor:Q'),
            color= alt.Color('load_source:N')
        ),
        alt.Chart(
            paretos_poland_env_lco2_investor,
            title= 'Poland - LCO2eq Investor'
        ).mark_line(
            size= 3,
            clip= True
        ).encode(
            x= alt.X('ress:Q').scale(domain= (0, 90)),
            y= alt.Y('lco2_investor:Q'),
            color= alt.Color('load_source:N')
        ),
        alt.Chart(
            paretos_sweden_env_lco2_investor,
            title= 'Sweden - LCO2eq Investor'
        ).mark_line(
            size= 3,
            clip= True
        ).encode(
            x= alt.X('ress:Q').scale(domain= (0, 90)),
            y= alt.Y('lco2_investor:Q'),
            color= alt.Color('load_source:N')
        )
    ),
    alt.hconcat(
        alt.Chart(
            paretos_italy_env_lco2_enduser,
            title= 'Italy - LCO2eq End User'
        ).mark_line(
            size= 3,
            clip= True
        ).encode(
            x= alt.X('ress:Q').scale(domain= (0, 90)),
            y= alt.Y('lco2_enduser:Q'),
            color= alt.Color('load_source:N')
        ),
        alt.Chart(
            paretos_poland_env_lco2_enduser,
            title= 'Poland - LCO2eq End User'
        ).mark_line(
            size= 3,
            clip= True
        ).encode(
            x= alt.X('ress:Q').scale(domain= (0, 90)),
            y= alt.Y('lco2_enduser:Q'),
            color= alt.Color('load_source:N')
        ),
        alt.Chart(
            paretos_sweden_env_lco2_enduser,
            title= 'Sweden - LCO2eq End User'
        ).mark_line(
            size= 3,
            clip= True
        ).encode(
            x= alt.X('ress:Q').scale(domain= (0, 90)),
            y= alt.Y('lco2_enduser:Q'),
            color= alt.Color('load_source:N')
        )
    ),
    alt.hconcat(
        alt.Chart(
            paretos_italy_env_lco2_investor,
            title= 'Italy - LCO2eq Investor'
        ).mark_line(
            size= 3,
            clip= True
        ).encode(
            x= alt.X('ress:Q').scale(domain= (0, 90)),
            y= alt.Y('lco2_investor:Q').scale(domain= (0, 100)),
            color= alt.Color('load_source:N')
        ),
        alt.Chart(
            paretos_poland_env_lco2_investor,
            title= 'Poland - LCO2eq Investor'
        ).mark_line(
            size= 3,
            clip= True
        ).encode(
            x= alt.X('ress:Q').scale(domain= (0, 90)),
            y= alt.Y('lco2_investor:Q').scale(domain= (0, 100)),
            color= alt.Color('load_source:N')
        ),
        alt.Chart(
            paretos_sweden_env_lco2_investor,
            title= 'Sweden - LCO2eq Investor'
        ).mark_line(
            size= 3,
            clip= True
        ).encode(
            x= alt.X('ress:Q').scale(domain= (0, 90)),
            y= alt.Y('lco2_investor:Q').scale(domain= (0, 100)),
            color= alt.Color('load_source:N')
        )
    ),
    alt.hconcat(
        alt.Chart(
            paretos_italy_env_lco2_enduser,
            title= 'Italy - LCO2eq End User'
        ).mark_line(
            size= 3,
            clip= True
        ).encode(
            x= alt.X('ress:Q').scale(domain= (0, 90)),
            y= alt.Y('lco2_enduser:Q').scale(domain= (0, 600)),
            color= alt.Color('load_source:N')
        ),
        alt.Chart(
            paretos_poland_env_lco2_enduser,
            title= 'Poland - LCO2eq End User'
        ).mark_line(
            size= 3,
            clip= True
        ).encode(
            x= alt.X('ress:Q').scale(domain= (0, 90)),
            y= alt.Y('lco2_enduser:Q').scale(domain= (0, 600)),
            color= alt.Color('load_source:N')
        ),
        alt.Chart(
            paretos_sweden_env_lco2_enduser,
            title= 'Sweden - LCO2eq End User'
        ).mark_line(
            size= 3,
            clip= True
        ).encode(
            x= alt.X('ress:Q').scale(domain= (0, 90)),
            y= alt.Y('lco2_enduser:Q').scale(domain= (0, 600)),
            color= alt.Color('load_source:N')
        )
    )
)

alt.VConcatChart(...)

___
### Paretos by Load

In [18]:
alt.vconcat(
    alt.hconcat(
        alt.Chart(
            paretos_residential4_econ_lcoe_investor,
            title= 'Residential - LCOE Investor'
        ).mark_line(
            size= 3
        ).encode(
            x= alt.X('ress:Q').scale(domain= (0, 80)),
            y= alt.Y('lcoe_investor:Q'),#.scale(domain= (0, 0.12)),
            color= alt.Color('region:N')
        ),
        alt.Chart(
            paretos_industrial2_econ_lcoe_investor,
            title= 'Industrial - LCOE Investor'
        ).mark_line(
            size= 3
        ).encode(
            x= alt.X('ress:Q').scale(domain= (0, 80)),
            y= alt.Y('lcoe_investor:Q'),#.scale(domain= (0, 0.12)),
            color= alt.Color('region:N')
        ),
        alt.Chart(
            paretos_industrial1_econ_lcoe_investor,
            title= 'Industrial Shift - LCOE Investor'
        ).mark_line(
            size= 3
        ).encode(
            x= alt.X('ress:Q').scale(domain= (0, 80)),
            y= alt.Y('lcoe_investor:Q'),#.scale(domain= (0, 0.12)),
            color= alt.Color('region:N')
        )
    ),
    alt.hconcat(
        alt.Chart(
            paretos_residential4_econ_lcoe_enduser,
            title= 'Residential - LCOE End User'
        ).mark_line(
            size= 3
        ).encode(
            x= alt.X('ress:Q').scale(domain= (0, 80)),
            y= alt.Y('lcoe_enduser:Q'),#.scale(domain= (0, 0.12)),
            color= alt.Color('region:N')
        ),
        alt.Chart(
            paretos_industrial2_econ_lcoe_enduser,
            title= 'Industrial - LCOE End User'
        ).mark_line(
            size= 3
        ).encode(
            x= alt.X('ress:Q').scale(domain= (0, 80)),
            y= alt.Y('lcoe_enduser:Q'),#.scale(domain= (0, 0.12)),
            color= alt.Color('region:N')
        ),
        alt.Chart(
            paretos_industrial1_econ_lcoe_enduser,
            title= 'Industrial Shift - LCOE End User'
        ).mark_line(
            size= 3
        ).encode(
            x= alt.X('ress:Q').scale(domain= (0, 80)),
            y= alt.Y('lcoe_enduser:Q'),#.scale(domain= (0, 0.12)),
            color= alt.Color('region:N')
        )
    )
)

alt.VConcatChart(...)

In [19]:
alt.vconcat(
    alt.hconcat(
        alt.Chart(
            paretos_residential4_env_lco2_investor,
            title= 'Residential - LCO2eq Investor'
        ).mark_line(
            size= 3
        ).encode(
            x= alt.X('ress:Q').scale(domain= (0, 80)),
            y= alt.Y('lco2_investor:Q'),#.scale(domain= (0, 0.12)),
            color= alt.Color('region:N')
        ),
        alt.Chart(
            paretos_industrial2_env_lco2_investor,
            title= 'Industrial - LCO2eq Investor'
        ).mark_line(
            size= 3
        ).encode(
            x= alt.X('ress:Q').scale(domain= (0, 80)),
            y= alt.Y('lco2_investor:Q'),#.scale(domain= (0, 0.12)),
            color= alt.Color('region:N')
        ),
        alt.Chart(
            paretos_industrial1_env_lco2_investor,
            title= 'Industrial Shift - LCO2eq Investor'
        ).mark_line(
            size= 3
        ).encode(
            x= alt.X('ress:Q').scale(domain= (0, 80)),
            y= alt.Y('lco2_investor:Q'),#.scale(domain= (0, 0.12)),
            color= alt.Color('region:N')
        )
    ),
    alt.hconcat(
        alt.Chart(
            paretos_residential4_env_lco2_enduser,
            title= 'Residential - LCO2eq End User'
        ).mark_line(
            size= 3
        ).encode(
            x= alt.X('ress:Q').scale(domain= (0, 80)),
            y= alt.Y('lco2_enduser:Q').scale(domain= (0, 600)),
            color= alt.Color('region:N')
        ),
        alt.Chart(
            paretos_industrial2_env_lco2_enduser,
            title= 'Industrial - LCO2eq End User'
        ).mark_line(
            size= 3
        ).encode(
            x= alt.X('ress:Q').scale(domain= (0, 80)),
            y= alt.Y('lco2_enduser:Q').scale(domain= (0, 600)),
            color= alt.Color('region:N')
        ),
        alt.Chart(
            paretos_industrial1_env_lco2_enduser,
            title= 'Industrial Shift - LCO2eq End User'
        ).mark_line(
            size= 3
        ).encode(
            x= alt.X('ress:Q').scale(domain= (0, 80)),
            y= alt.Y('lco2_enduser:Q').scale(domain= (0, 600)),
            color= alt.Color('region:N')
        )
    )
)

alt.VConcatChart(...)

___
___
### Iso-Pareto curves

##### Base case - Sweden for residential load

In [43]:
paretos_basecase_econ_p_pv=     pd.concat(
    [
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_PV', 0.5, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_PV', 1.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_PV', 1.5, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_PV', 2.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_PV', 2.5, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_PV', 3.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_PV', 3.5, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_PV', 4.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_PV', 4.5, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_PV', 5.0, 'lcoe_investor', 'ress'),
    ]
)
paretos_basecase_econ_p_bess=   pd.concat(
    [
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_BESS', 0.5, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_BESS', 1.0, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_BESS', 1.5, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_BESS', 2.0, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_BESS', 2.5, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_BESS', 3.0, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_BESS', 3.5, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_BESS', 4.0, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_BESS', 4.5, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_BESS', 5.0, 'lcoe_investor', 'ress'),
    ]
)
paretos_basecase_econ_t_bess=   pd.concat(
    [
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'T_BESS', 0, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'T_BESS', 1, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'T_BESS', 2, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'T_BESS', 3, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'T_BESS', 4, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'T_BESS', 5, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'T_BESS', 6, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'T_BESS', 7, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'T_BESS', 8, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'T_BESS', 9, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'T_BESS', 10, 'lcoe_investor', 'ress')
    ]
)

paretos_basecase_env_p_pv=      pd.concat(
    [
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_PV', 0.5, 'lco2_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_PV', 1.0, 'lco2_investor', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_PV', 1.5, 'lco2_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_PV', 2.0, 'lco2_investor', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_PV', 2.5, 'lco2_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_PV', 3.0, 'lco2_investor', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_PV', 3.5, 'lco2_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_PV', 4.0, 'lco2_investor', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_PV', 4.5, 'lco2_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_PV', 5.0, 'lco2_investor', 'ress'),
    ]
)
paretos_basecase_env_p_bess=    pd.concat(
    [
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_BESS', 0.5, 'lco2_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_BESS', 1.0, 'lco2_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_BESS', 1.5, 'lco2_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_BESS', 2.0, 'lco2_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_BESS', 2.5, 'lco2_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_BESS', 3.0, 'lco2_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_BESS', 3.5, 'lco2_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_BESS', 4.0, 'lco2_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_BESS', 4.5, 'lco2_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_BESS', 5.0, 'lco2_investor', 'ress'),
    ]
)
paretos_basecase_env_t_bess=    pd.concat(
    [
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'T_BESS', 0, 'lco2_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'T_BESS', 1, 'lco2_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'T_BESS', 2, 'lco2_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'T_BESS', 3, 'lco2_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'T_BESS', 4, 'lco2_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'T_BESS', 5, 'lco2_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'T_BESS', 6, 'lco2_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'T_BESS', 7, 'lco2_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'T_BESS', 8, 'lco2_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'T_BESS', 9, 'lco2_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'T_BESS', 10, 'lco2_investor', 'ress')
    ]
)



paretos_basecase_econ_e_bess=    pd.concat(
    [
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 0.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 0.5, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 1.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 1.5, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 2.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 2.5, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 3.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 3.5, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 4.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 4.5, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 5.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 6.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 7.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 7.5, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 8.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 9.0, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 10.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 10.5, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 12.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 12.5, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 13.5, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 14.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 15.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 16.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 17.5, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 18.0, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 20.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 21.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 22.5, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 24.0, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 25.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 27.0, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 30.0, 'lcoe_investor', 'ress'),
    ]
)
paretos_basecase_env_e_bess=    pd.concat(
    [
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 0.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 0.5, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 1.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 1.5, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 2.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 2.5, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 3.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 3.5, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 4.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 4.5, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 5.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 6.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 7.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 7.5, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 8.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 9.0, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 10.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 10.5, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 12.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 12.5, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 13.5, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 14.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 15.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 16.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 17.5, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 18.0, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 20.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 21.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 22.5, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 24.0, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 25.0, 'lcoe_investor', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 27.0, 'lcoe_investor', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 30.0, 'lcoe_investor', 'ress'),
    ]
)

In [44]:
# paretos_basecase_econ_p_pv= remove_rows_above_specific_value(paretos_basecase_econ_p_pv, 'lcoe_investor', 0.15)
# paretos_basecase_env_p_pv=  remove_rows_above_specific_value(paretos_basecase_env_p_pv, 'lcoe_investor', 0.15)
# paretos_basecase_econ_p_pv= remove_rows_above_specific_value(paretos_basecase_econ_p_pv, 'P_BESS', 3.0)
# paretos_basecase_env_p_pv=  remove_rows_above_specific_value(paretos_basecase_env_p_pv, 'P_BESS', 3.0)



lines_econ_lcoe=  alt.Chart(
    paretos_basecase_econ_p_pv,
    title= 'LCOE - Investor'
).mark_line(interpolate= 'cardinal').encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lcoe_investor:Q',
        axis= alt.Axis(
            title= 'Levelised Cost Of Energy [EUR/kWh]'
        )
    ),
    color= alt.Color('P_PV:Q').scale(scheme= 'reds'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)
points_econ_lcoe= alt.Chart(paretos_basecase_econ_p_pv).mark_circle().encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lcoe_investor:Q',
        axis= alt.Axis(
            title= 'Levelised Cost Of Energy [EUR/kWh]'
        )
    ),
    color= alt.Color('P_PV:Q').scale(scheme= 'reds'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)

lines_env_lcoe=  alt.Chart(
    paretos_basecase_env_p_pv,
    title= 'LCOE - Investor'
).mark_line(interpolate= 'cardinal').encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lcoe_investor:Q',
        axis= alt.Axis(
            title= 'Levelised Cost Of Energy [EUR/kWh]'
        )
    ),
    color= alt.Color('P_PV:Q').scale(scheme= 'greens'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)
points_env_lcoe= alt.Chart(paretos_basecase_env_p_pv).mark_circle().encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lcoe_investor:Q',
        axis= alt.Axis(
            title= 'Levelised Cost Of Energy [EUR/kWh]'
        )
    ),
    color= alt.Color('P_PV:Q').scale(scheme= 'greens'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)


lines_econ_lco2=  alt.Chart(
    paretos_basecase_econ_p_pv,
    title= 'LCO2 - Investor'
).mark_line(interpolate= 'cardinal').encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lco2_investor:Q',
        axis= alt.Axis(
            title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
        )
    ),
    color= alt.Color('P_PV:Q').scale(scheme= 'reds'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)
points_econ_lco2= alt.Chart(paretos_basecase_econ_p_pv).mark_circle().encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lco2_investor:Q',
        axis= alt.Axis(
            title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
        )
    ),
    color= alt.Color('P_PV:Q').scale(scheme= 'reds'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)

lines_env_lco2=  alt.Chart(
    paretos_basecase_env_p_pv,
    title= 'LCO2 - Investor'
).mark_line(interpolate= 'cardinal').encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lco2_investor:Q',
        axis= alt.Axis(
            title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
        )
    ),
    color= alt.Color('P_PV:Q').scale(scheme= 'greens'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)
points_env_lco2= alt.Chart(paretos_basecase_env_p_pv).mark_circle().encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lco2_investor:Q',
        axis= alt.Axis(
            title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
        )
    ),
    color= alt.Color('P_PV:Q').scale(scheme= 'greens'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)





alt.hconcat(
    alt.layer(
        alt.layer(
            lines_econ_lcoe,
            points_econ_lcoe
        ),#.resolve_scale(color= 'independent'),
        alt.layer(
            lines_env_lcoe,
            points_env_lcoe
        )#.resolve_scale(color= 'independent')
    ).resolve_scale(color= 'independent'),
    alt.layer(
        alt.layer(
            lines_econ_lco2,
            points_econ_lco2
        ),#.resolve_scale(color= 'independent'),
        alt.layer(
            lines_env_lco2,
            points_env_lco2
        )#.resolve_scale(color= 'independent')
    ).resolve_scale(color= 'independent'),
)

alt.HConcatChart(...)

In [47]:
# paretos_basecase_econ_p_bess= remove_rows_above_specific_value(paretos_basecase_econ_p_bess, 'lcoe_investor', 0.15)
# paretos_basecase_env_p_bess=  remove_rows_above_specific_value(paretos_basecase_env_p_bess, 'lcoe_investor', 0.15)
# paretos_basecase_econ_p_bess= remove_rows_above_specific_value(paretos_basecase_econ_p_bess, 'P_BESS', 3)
# paretos_basecase_env_p_bess=  remove_rows_above_specific_value(paretos_basecase_env_p_bess, 'P_BESS', 3)



lines_econ_lcoe=  alt.Chart(
    paretos_basecase_econ_p_bess,
    title= 'LCOE - Investor'
).mark_line(interpolate= 'cardinal').encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lcoe_investor:Q',
        axis= alt.Axis(
            title= 'Levelised Cost Of Energy [EUR/kWh]'
        )
    ),
    color= alt.Color('P_BESS:Q').scale(scheme= 'reds'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)
points_econ_lcoe= alt.Chart(paretos_basecase_econ_p_bess).mark_circle().encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lcoe_investor:Q',
        axis= alt.Axis(
            title= 'Levelised Cost Of Energy [EUR/kWh]'
        )
    ),
    color= alt.Color('P_BESS:Q').scale(scheme= 'reds'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)

lines_env_lcoe=  alt.Chart(
    paretos_basecase_env_p_bess,
    title= 'LCOE - Investor'
).mark_line(interpolate= 'cardinal').encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lcoe_investor:Q',
        axis= alt.Axis(
            title= 'Levelised Cost Of Energy [EUR/kWh]'
        )
    ),
    color= alt.Color('P_BESS:Q').scale(scheme= 'greens'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)
points_env_lcoe= alt.Chart(paretos_basecase_env_p_bess).mark_circle().encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lcoe_investor:Q',
        axis= alt.Axis(
            title= 'Levelised Cost Of Energy [EUR/kWh]'
        )
    ),
    color= alt.Color('P_BESS:Q').scale(scheme= 'greens'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)


lines_econ_lco2=  alt.Chart(
    paretos_basecase_econ_p_bess,
    title= 'LCO2 - Investor'
).mark_line(interpolate= 'cardinal').encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lco2_investor:Q',
        axis= alt.Axis(
            title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
        )
    ),
    color= alt.Color('P_BESS:Q').scale(scheme= 'reds'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)
points_econ_lco2= alt.Chart(paretos_basecase_econ_p_bess).mark_circle().encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lco2_investor:Q',
        axis= alt.Axis(
            title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
        )
    ),
    color= alt.Color('P_BESS:Q').scale(scheme= 'reds'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)

lines_env_lco2=  alt.Chart(
    paretos_basecase_env_p_bess,
    title= 'LCO2 - Investor'
).mark_line(interpolate= 'cardinal').encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lco2_investor:Q',
        axis= alt.Axis(
            title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
        )
    ),
    color= alt.Color('P_BESS:Q').scale(scheme= 'greens'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)
points_env_lco2= alt.Chart(paretos_basecase_env_p_bess).mark_circle().encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lco2_investor:Q',
        axis= alt.Axis(
            title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
        )
    ),
    color= alt.Color('P_BESS:Q').scale(scheme= 'greens'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)





alt.hconcat(
    alt.layer(
        alt.layer(
            lines_econ_lcoe,
            points_econ_lcoe
        ),#.resolve_scale(color= 'independent'),
        alt.layer(
            lines_env_lcoe,
            points_env_lcoe
        )#.resolve_scale(color= 'independent')
    ).resolve_scale(color= 'independent'),
    alt.layer(
        alt.layer(
            lines_econ_lco2,
            points_econ_lco2
        ),#.resolve_scale(color= 'independent'),
        alt.layer(
            lines_env_lco2,
            points_env_lco2
        )#.resolve_scale(color= 'independent')
    ).resolve_scale(color= 'independent'),
)

alt.HConcatChart(...)

In [48]:
# paretos_basecase_econ_t_bess= remove_rows_above_specific_value(paretos_basecase_econ_t_bess, 'lcoe_investor', 0.15)
# paretos_basecase_env_t_bess=  remove_rows_above_specific_value(paretos_basecase_env_t_bess, 'lcoe_investor', 0.15)
# paretos_basecase_econ_t_bess= remove_rows_above_specific_value(paretos_basecase_econ_t_bess, 'P_BESS', 3)
# paretos_basecase_env_t_bess=  remove_rows_above_specific_value(paretos_basecase_env_t_bess, 'P_BESS', 3)



lines_econ_lcoe=  alt.Chart(
    paretos_basecase_econ_t_bess,
    title= 'LCOE - Investor'
).mark_line(interpolate= 'cardinal').encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lcoe_investor:Q',
        axis= alt.Axis(
            title= 'Levelised Cost Of Energy [EUR/kWh]'
        )
    ),
    color= alt.Color('T_BESS:Q').scale(scheme= 'reds'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)
points_econ_lcoe= alt.Chart(paretos_basecase_econ_t_bess).mark_circle().encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lcoe_investor:Q',
        axis= alt.Axis(
            title= 'Levelised Cost Of Energy [EUR/kWh]'
        )
    ),
    color= alt.Color('T_BESS:Q').scale(scheme= 'reds'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)

lines_env_lcoe=  alt.Chart(
    paretos_basecase_env_t_bess,
    title= 'LCOE - Investor'
).mark_line(interpolate= 'cardinal').encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lcoe_investor:Q',
        axis= alt.Axis(
            title= 'Levelised Cost Of Energy [EUR/kWh]'
        )
    ),
    color= alt.Color('T_BESS:Q').scale(scheme= 'greens'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)
points_env_lcoe= alt.Chart(paretos_basecase_env_t_bess).mark_circle().encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lcoe_investor:Q',
        axis= alt.Axis(
            title= 'Levelised Cost Of Energy [EUR/kWh]'
        )
    ),
    color= alt.Color('T_BESS:Q').scale(scheme= 'greens'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)


lines_econ_lco2=  alt.Chart(
    paretos_basecase_econ_t_bess,
    title= 'LCO2 - Investor'
).mark_line(interpolate= 'cardinal').encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lco2_investor:Q',
        axis= alt.Axis(
            title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
        )
    ),
    color= alt.Color('T_BESS:Q').scale(scheme= 'reds'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)
points_econ_lco2= alt.Chart(paretos_basecase_econ_t_bess).mark_circle().encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lco2_investor:Q',
        axis= alt.Axis(
            title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
        )
    ),
    color= alt.Color('T_BESS:Q').scale(scheme= 'reds'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)

lines_env_lco2=  alt.Chart(
    paretos_basecase_env_t_bess,
    title= 'LCO2 - Investor'
).mark_line(interpolate= 'cardinal').encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lco2_investor:Q',
        axis= alt.Axis(
            title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
        )
    ),
    color= alt.Color('T_BESS:Q').scale(scheme= 'greens'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)
points_env_lco2= alt.Chart(paretos_basecase_env_t_bess).mark_circle().encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lco2_investor:Q',
        axis= alt.Axis(
            title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
        )
    ),
    color= alt.Color('T_BESS:Q').scale(scheme= 'greens'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)





alt.hconcat(
    alt.layer(
        alt.layer(
            lines_econ_lcoe,
            points_econ_lcoe
        ),#.resolve_scale(color= 'independent'),
        alt.layer(
            lines_env_lcoe,
            points_env_lcoe
        )#.resolve_scale(color= 'independent')
    ).resolve_scale(color= 'independent'),
    alt.layer(
        alt.layer(
            lines_econ_lco2,
            points_econ_lco2
        ),#.resolve_scale(color= 'independent'),
        alt.layer(
            lines_env_lco2,
            points_env_lco2
        )#.resolve_scale(color= 'independent')
    ).resolve_scale(color= 'independent'),
)

alt.HConcatChart(...)

In [49]:
# paretos_basecase_econ_e_bess= remove_rows_above_specific_value(paretos_basecase_econ_e_bess, 'lcoe_investor', 0.15)
# paretos_basecase_env_e_bess=  remove_rows_above_specific_value(paretos_basecase_env_e_bess, 'lcoe_investor', 0.15)
# paretos_basecase_econ_e_bess= remove_rows_above_specific_value(paretos_basecase_econ_e_bess, 'P_BESS', 3)
# paretos_basecase_env_e_bess=  remove_rows_above_specific_value(paretos_basecase_env_e_bess, 'P_BESS', 3)



lines_econ_lcoe=  alt.Chart(
    paretos_basecase_econ_e_bess,
    title= 'LCOE - Investor'
).mark_line(interpolate= 'cardinal').encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lcoe_investor:Q',
        axis= alt.Axis(
            title= 'Levelised Cost Of Energy [EUR/kWh]'
        )
    ),
    color= alt.Color('E_BESS:Q').scale(scheme= 'reds'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)
points_econ_lcoe= alt.Chart(paretos_basecase_econ_e_bess).mark_circle().encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lcoe_investor:Q',
        axis= alt.Axis(
            title= 'Levelised Cost Of Energy [EUR/kWh]'
        )
    ),
    color= alt.Color('E_BESS:Q').scale(scheme= 'reds'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)

lines_env_lcoe=  alt.Chart(
    paretos_basecase_env_e_bess,
    title= 'LCOE - Investor'
).mark_line(interpolate= 'cardinal').encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lcoe_investor:Q',
        axis= alt.Axis(
            title= 'Levelised Cost Of Energy [EUR/kWh]'
        )
    ),
    color= alt.Color('E_BESS:Q').scale(scheme= 'greens'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)
points_env_lcoe= alt.Chart(paretos_basecase_env_e_bess).mark_circle().encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lcoe_investor:Q',
        axis= alt.Axis(
            title= 'Levelised Cost Of Energy [EUR/kWh]'
        )
    ),
    color= alt.Color('E_BESS:Q').scale(scheme= 'greens'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)


lines_econ_lco2=  alt.Chart(
    paretos_basecase_econ_e_bess,
    title= 'LCO2 - Investor'
).mark_line(interpolate= 'cardinal').encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lco2_investor:Q',
        axis= alt.Axis(
            title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
        )
    ),
    color= alt.Color('E_BESS:Q').scale(scheme= 'reds'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)
points_econ_lco2= alt.Chart(paretos_basecase_econ_e_bess).mark_circle().encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lco2_investor:Q',
        axis= alt.Axis(
            title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
        )
    ),
    color= alt.Color('E_BESS:Q').scale(scheme= 'reds'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)

lines_env_lco2=  alt.Chart(
    paretos_basecase_env_e_bess,
    title= 'LCO2 - Investor'
).mark_line(interpolate= 'cardinal').encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lco2_investor:Q',
        axis= alt.Axis(
            title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
        )
    ),
    color= alt.Color('E_BESS:Q').scale(scheme= 'greens'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)
points_env_lco2= alt.Chart(paretos_basecase_env_e_bess).mark_circle().encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lco2_investor:Q',
        axis= alt.Axis(
            title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
        )
    ),
    color= alt.Color('E_BESS:Q').scale(scheme= 'greens'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)





alt.hconcat(
    alt.layer(
        alt.layer(
            lines_econ_lcoe,
            points_econ_lcoe
        ),#.resolve_scale(color= 'independent'),
        alt.layer(
            lines_env_lcoe,
            points_env_lcoe
        )#.resolve_scale(color= 'independent')
    ).resolve_scale(color= 'independent'),
    alt.layer(
        alt.layer(
            lines_econ_lco2,
            points_econ_lco2
        ),#.resolve_scale(color= 'independent'),
        alt.layer(
            lines_env_lco2,
            points_env_lco2
        )#.resolve_scale(color= 'independent')
    ).resolve_scale(color= 'independent'),
)

alt.HConcatChart(...)

In [52]:
paretos_basecase_econ_p_pv=     pd.concat(
    [
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_PV', 0.5, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_PV', 1.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_PV', 1.5, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_PV', 2.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_PV', 2.5, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_PV', 3.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_PV', 3.5, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_PV', 4.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_PV', 4.5, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_PV', 5.0, 'lcoe_enduser', 'ress'),
    ]
)
paretos_basecase_econ_p_bess=   pd.concat(
    [
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_BESS', 0.5, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_BESS', 1.0, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_BESS', 1.5, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_BESS', 2.0, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_BESS', 2.5, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_BESS', 3.0, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_BESS', 3.5, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_BESS', 4.0, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_BESS', 4.5, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'P_BESS', 5.0, 'lcoe_enduser', 'ress'),
    ]
)
paretos_basecase_econ_t_bess=   pd.concat(
    [
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'T_BESS', 0, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'T_BESS', 1, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'T_BESS', 2, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'T_BESS', 3, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'T_BESS', 4, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'T_BESS', 5, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'T_BESS', 6, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'T_BESS', 7, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'T_BESS', 8, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'T_BESS', 9, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'T_BESS', 10, 'lcoe_enduser', 'ress')
    ]
)

paretos_basecase_env_p_pv=      pd.concat(
    [
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_PV', 0.5, 'lco2_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_PV', 1.0, 'lco2_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_PV', 1.5, 'lco2_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_PV', 2.0, 'lco2_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_PV', 2.5, 'lco2_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_PV', 3.0, 'lco2_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_PV', 3.5, 'lco2_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_PV', 4.0, 'lco2_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_PV', 4.5, 'lco2_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_PV', 5.0, 'lco2_enduser', 'ress'),
    ]
)
paretos_basecase_env_p_bess=    pd.concat(
    [
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_BESS', 0.5, 'lco2_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_BESS', 1.0, 'lco2_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_BESS', 1.5, 'lco2_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_BESS', 2.0, 'lco2_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_BESS', 2.5, 'lco2_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_BESS', 3.0, 'lco2_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_BESS', 3.5, 'lco2_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_BESS', 4.0, 'lco2_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_BESS', 4.5, 'lco2_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'P_BESS', 5.0, 'lco2_enduser', 'ress'),
    ]
)
paretos_basecase_env_t_bess=    pd.concat(
    [
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'T_BESS', 0, 'lco2_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'T_BESS', 1, 'lco2_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'T_BESS', 2, 'lco2_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'T_BESS', 3, 'lco2_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'T_BESS', 4, 'lco2_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'T_BESS', 5, 'lco2_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'T_BESS', 6, 'lco2_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'T_BESS', 7, 'lco2_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'T_BESS', 8, 'lco2_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'T_BESS', 9, 'lco2_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'T_BESS', 10, 'lco2_enduser', 'ress')
    ]
)



paretos_basecase_econ_e_bess=    pd.concat(
    [
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 0.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 0.5, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 1.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 1.5, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 2.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 2.5, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 3.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 3.5, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 4.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 4.5, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 5.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 6.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 7.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 7.5, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 8.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 9.0, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 10.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 10.5, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 12.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 12.5, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 13.5, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 14.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 15.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 16.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 17.5, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 18.0, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 20.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 21.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 22.5, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 24.0, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 25.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 27.0, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_econ_sweden, 'SE', 'residential4', 'E_BESS', 30.0, 'lcoe_enduser', 'ress'),
    ]
)
paretos_basecase_env_e_bess=    pd.concat(
    [
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 0.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 0.5, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 1.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 1.5, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 2.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 2.5, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 3.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 3.5, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 4.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 4.5, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 5.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 6.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 7.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 7.5, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 8.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 9.0, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 10.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 10.5, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 12.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 12.5, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 13.5, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 14.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 15.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 16.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 17.5, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 18.0, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 20.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 21.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 22.5, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 24.0, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 25.0, 'lcoe_enduser', 'ress'),
        #extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 27.0, 'lcoe_enduser', 'ress'),
        extract_pareto_front_isocurve(results_env_sweden, 'SE', 'residential4', 'E_BESS', 30.0, 'lcoe_enduser', 'ress'),
    ]
)

In [53]:
# paretos_basecase_econ_p_pv= remove_rows_above_specific_value(paretos_basecase_econ_p_pv, 'lcoe_enduser', 0.15)
# paretos_basecase_env_p_pv=  remove_rows_above_specific_value(paretos_basecase_env_p_pv, 'lcoe_enduser', 0.15)
# paretos_basecase_econ_p_pv= remove_rows_above_specific_value(paretos_basecase_econ_p_pv, 'P_BESS', 3.0)
# paretos_basecase_env_p_pv=  remove_rows_above_specific_value(paretos_basecase_env_p_pv, 'P_BESS', 3.0)



lines_econ_lcoe=  alt.Chart(
    paretos_basecase_econ_p_pv,
    title= 'LCOE - End User'
).mark_line(interpolate= 'cardinal').encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lcoe_enduser:Q',
        axis= alt.Axis(
            title= 'Levelised Cost Of Energy [EUR/kWh]'
        )
    ),
    color= alt.Color('P_PV:Q').scale(scheme= 'reds'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)
points_econ_lcoe= alt.Chart(paretos_basecase_econ_p_pv).mark_circle().encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lcoe_enduser:Q',
        axis= alt.Axis(
            title= 'Levelised Cost Of Energy [EUR/kWh]'
        )
    ),
    color= alt.Color('P_PV:Q').scale(scheme= 'reds'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)

lines_env_lcoe=  alt.Chart(
    paretos_basecase_env_p_pv,
    title= 'LCOE - End User'
).mark_line(interpolate= 'cardinal').encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lcoe_enduser:Q',
        axis= alt.Axis(
            title= 'Levelised Cost Of Energy [EUR/kWh]'
        )
    ),
    color= alt.Color('P_PV:Q').scale(scheme= 'greens'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)
points_env_lcoe= alt.Chart(paretos_basecase_env_p_pv).mark_circle().encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lcoe_enduser:Q',
        axis= alt.Axis(
            title= 'Levelised Cost Of Energy [EUR/kWh]'
        )
    ),
    color= alt.Color('P_PV:Q').scale(scheme= 'greens'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)


lines_econ_lco2=  alt.Chart(
    paretos_basecase_econ_p_pv,
    title= 'LCO2 - End User'
).mark_line(interpolate= 'cardinal').encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lco2_enduser:Q',
        axis= alt.Axis(
            title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
        )
    ),
    color= alt.Color('P_PV:Q').scale(scheme= 'reds'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)
points_econ_lco2= alt.Chart(paretos_basecase_econ_p_pv).mark_circle().encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lco2_enduser:Q',
        axis= alt.Axis(
            title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
        )
    ),
    color= alt.Color('P_PV:Q').scale(scheme= 'reds'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)

lines_env_lco2=  alt.Chart(
    paretos_basecase_env_p_pv,
    title= 'LCO2 - End User'
).mark_line(interpolate= 'cardinal').encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lco2_enduser:Q',
        axis= alt.Axis(
            title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
        )
    ),
    color= alt.Color('P_PV:Q').scale(scheme= 'greens'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)
points_env_lco2= alt.Chart(paretos_basecase_env_p_pv).mark_circle().encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lco2_enduser:Q',
        axis= alt.Axis(
            title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
        )
    ),
    color= alt.Color('P_PV:Q').scale(scheme= 'greens'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)





alt.hconcat(
    alt.layer(
        alt.layer(
            lines_econ_lcoe,
            points_econ_lcoe
        ),#.resolve_scale(color= 'independent'),
        alt.layer(
            lines_env_lcoe,
            points_env_lcoe
        )#.resolve_scale(color= 'independent')
    ).resolve_scale(color= 'independent'),
    alt.layer(
        alt.layer(
            lines_econ_lco2,
            points_econ_lco2
        ),#.resolve_scale(color= 'independent'),
        alt.layer(
            lines_env_lco2,
            points_env_lco2
        )#.resolve_scale(color= 'independent')
    ).resolve_scale(color= 'independent'),
)

alt.HConcatChart(...)

In [56]:
#paretos_basecase_econ_p_bess= remove_rows_above_specific_value(paretos_basecase_econ_p_bess, 'lcoe_enduser', 0.15)
#paretos_basecase_env_p_bess=  remove_rows_above_specific_value(paretos_basecase_env_p_bess, 'lcoe_enduser', 0.15)
paretos_basecase_econ_p_bess= remove_rows_above_specific_value(paretos_basecase_econ_p_bess, 'P_BESS', 3)
paretos_basecase_env_p_bess=  remove_rows_above_specific_value(paretos_basecase_env_p_bess, 'P_BESS', 3)



lines_econ_lcoe=  alt.Chart(
    paretos_basecase_econ_p_bess,
    title= 'LCOE - End User'
).mark_line(interpolate= 'cardinal').encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lcoe_enduser:Q',
        axis= alt.Axis(
            title= 'Levelised Cost Of Energy [EUR/kWh]'
        )
    ),
    color= alt.Color('P_BESS:Q').scale(scheme= 'reds'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)
points_econ_lcoe= alt.Chart(paretos_basecase_econ_p_bess).mark_circle().encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lcoe_enduser:Q',
        axis= alt.Axis(
            title= 'Levelised Cost Of Energy [EUR/kWh]'
        )
    ),
    color= alt.Color('P_BESS:Q').scale(scheme= 'reds'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)

lines_env_lcoe=  alt.Chart(
    paretos_basecase_env_p_bess,
    title= 'LCOE - End User'
).mark_line(interpolate= 'cardinal').encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lcoe_enduser:Q',
        axis= alt.Axis(
            title= 'Levelised Cost Of Energy [EUR/kWh]'
        )
    ),
    color= alt.Color('P_BESS:Q').scale(scheme= 'greens'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)
points_env_lcoe= alt.Chart(paretos_basecase_env_p_bess).mark_circle().encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lcoe_enduser:Q',
        axis= alt.Axis(
            title= 'Levelised Cost Of Energy [EUR/kWh]'
        )
    ),
    color= alt.Color('P_BESS:Q').scale(scheme= 'greens'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)


lines_econ_lco2=  alt.Chart(
    paretos_basecase_econ_p_bess,
    title= 'LCO2 - End User'
).mark_line(interpolate= 'cardinal').encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lco2_enduser:Q',
        axis= alt.Axis(
            title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
        )
    ),
    color= alt.Color('P_BESS:Q').scale(scheme= 'reds'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)
points_econ_lco2= alt.Chart(paretos_basecase_econ_p_bess).mark_circle().encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lco2_enduser:Q',
        axis= alt.Axis(
            title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
        )
    ),
    color= alt.Color('P_BESS:Q').scale(scheme= 'reds'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)

lines_env_lco2=  alt.Chart(
    paretos_basecase_env_p_bess,
    title= 'LCO2 - End User'
).mark_line(interpolate= 'cardinal').encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lco2_enduser:Q',
        axis= alt.Axis(
            title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
        )
    ),
    color= alt.Color('P_BESS:Q').scale(scheme= 'greens'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)
points_env_lco2= alt.Chart(paretos_basecase_env_p_bess).mark_circle().encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lco2_enduser:Q',
        axis= alt.Axis(
            title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
        )
    ),
    color= alt.Color('P_BESS:Q').scale(scheme= 'greens'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)





alt.hconcat(
    alt.layer(
        alt.layer(
            lines_econ_lcoe,
            points_econ_lcoe
        ),#.resolve_scale(color= 'independent'),
        alt.layer(
            lines_env_lcoe,
            points_env_lcoe
        )#.resolve_scale(color= 'independent')
    ).resolve_scale(color= 'independent'),
    alt.layer(
        alt.layer(
            lines_econ_lco2,
            points_econ_lco2
        ),#.resolve_scale(color= 'independent'),
        alt.layer(
            lines_env_lco2,
            points_env_lco2
        )#.resolve_scale(color= 'independent')
    ).resolve_scale(color= 'independent'),
)

alt.HConcatChart(...)

In [57]:
#paretos_basecase_econ_t_bess= remove_rows_above_specific_value(paretos_basecase_econ_t_bess, 'lcoe_enduser', 0.15)
#paretos_basecase_env_t_bess=  remove_rows_above_specific_value(paretos_basecase_env_t_bess, 'lcoe_enduser', 0.15)
paretos_basecase_econ_t_bess= remove_rows_above_specific_value(paretos_basecase_econ_t_bess, 'P_BESS', 3)
paretos_basecase_env_t_bess=  remove_rows_above_specific_value(paretos_basecase_env_t_bess, 'P_BESS', 3)



lines_econ_lcoe=  alt.Chart(
    paretos_basecase_econ_t_bess,
    title= 'LCOE - End User'
).mark_line(interpolate= 'cardinal').encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lcoe_enduser:Q',
        axis= alt.Axis(
            title= 'Levelised Cost Of Energy [EUR/kWh]'
        )
    ),
    color= alt.Color('T_BESS:Q').scale(scheme= 'reds'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)
points_econ_lcoe= alt.Chart(paretos_basecase_econ_t_bess).mark_circle().encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lcoe_enduser:Q',
        axis= alt.Axis(
            title= 'Levelised Cost Of Energy [EUR/kWh]'
        )
    ),
    color= alt.Color('T_BESS:Q').scale(scheme= 'reds'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)

lines_env_lcoe=  alt.Chart(
    paretos_basecase_env_t_bess,
    title= 'LCOE - End User'
).mark_line(interpolate= 'cardinal').encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lcoe_enduser:Q',
        axis= alt.Axis(
            title= 'Levelised Cost Of Energy [EUR/kWh]'
        )
    ),
    color= alt.Color('T_BESS:Q').scale(scheme= 'greens'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)
points_env_lcoe= alt.Chart(paretos_basecase_env_t_bess).mark_circle().encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lcoe_enduser:Q',
        axis= alt.Axis(
            title= 'Levelised Cost Of Energy [EUR/kWh]'
        )
    ),
    color= alt.Color('T_BESS:Q').scale(scheme= 'greens'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)


lines_econ_lco2=  alt.Chart(
    paretos_basecase_econ_t_bess,
    title= 'LCO2 - End User'
).mark_line(interpolate= 'cardinal').encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lco2_enduser:Q',
        axis= alt.Axis(
            title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
        )
    ),
    color= alt.Color('T_BESS:Q').scale(scheme= 'reds'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)
points_econ_lco2= alt.Chart(paretos_basecase_econ_t_bess).mark_circle().encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lco2_enduser:Q',
        axis= alt.Axis(
            title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
        )
    ),
    color= alt.Color('T_BESS:Q').scale(scheme= 'reds'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)

lines_env_lco2=  alt.Chart(
    paretos_basecase_env_t_bess,
    title= 'LCO2 - End User'
).mark_line(interpolate= 'cardinal').encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lco2_enduser:Q',
        axis= alt.Axis(
            title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
        )
    ),
    color= alt.Color('T_BESS:Q').scale(scheme= 'greens'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)
points_env_lco2= alt.Chart(paretos_basecase_env_t_bess).mark_circle().encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lco2_enduser:Q',
        axis= alt.Axis(
            title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
        )
    ),
    color= alt.Color('T_BESS:Q').scale(scheme= 'greens'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)





alt.hconcat(
    alt.layer(
        alt.layer(
            lines_econ_lcoe,
            points_econ_lcoe
        ),#.resolve_scale(color= 'independent'),
        alt.layer(
            lines_env_lcoe,
            points_env_lcoe
        )#.resolve_scale(color= 'independent')
    ).resolve_scale(color= 'independent'),
    alt.layer(
        alt.layer(
            lines_econ_lco2,
            points_econ_lco2
        ),#.resolve_scale(color= 'independent'),
        alt.layer(
            lines_env_lco2,
            points_env_lco2
        )#.resolve_scale(color= 'independent')
    ).resolve_scale(color= 'independent'),
)

alt.HConcatChart(...)

In [58]:
#paretos_basecase_econ_e_bess= remove_rows_above_specific_value(paretos_basecase_econ_e_bess, 'lcoe_enduser', 0.15)
#paretos_basecase_env_e_bess=  remove_rows_above_specific_value(paretos_basecase_env_e_bess, 'lcoe_enduser', 0.15)
paretos_basecase_econ_e_bess= remove_rows_above_specific_value(paretos_basecase_econ_e_bess, 'P_BESS', 3)
paretos_basecase_env_e_bess=  remove_rows_above_specific_value(paretos_basecase_env_e_bess, 'P_BESS', 3)



lines_econ_lcoe=  alt.Chart(
    paretos_basecase_econ_e_bess,
    title= 'LCOE - End User'
).mark_line(interpolate= 'cardinal').encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lcoe_enduser:Q',
        axis= alt.Axis(
            title= 'Levelised Cost Of Energy [EUR/kWh]'
        )
    ),
    color= alt.Color('E_BESS:Q').scale(scheme= 'reds'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)
points_econ_lcoe= alt.Chart(paretos_basecase_econ_e_bess).mark_circle().encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lcoe_enduser:Q',
        axis= alt.Axis(
            title= 'Levelised Cost Of Energy [EUR/kWh]'
        )
    ),
    color= alt.Color('E_BESS:Q').scale(scheme= 'reds'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)

lines_env_lcoe=  alt.Chart(
    paretos_basecase_env_e_bess,
    title= 'LCOE - End User'
).mark_line(interpolate= 'cardinal').encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lcoe_enduser:Q',
        axis= alt.Axis(
            title= 'Levelised Cost Of Energy [EUR/kWh]'
        )
    ),
    color= alt.Color('E_BESS:Q').scale(scheme= 'greens'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)
points_env_lcoe= alt.Chart(paretos_basecase_env_e_bess).mark_circle().encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lcoe_enduser:Q',
        axis= alt.Axis(
            title= 'Levelised Cost Of Energy [EUR/kWh]'
        )
    ),
    color= alt.Color('E_BESS:Q').scale(scheme= 'greens'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)


lines_econ_lco2=  alt.Chart(
    paretos_basecase_econ_e_bess,
    title= 'LCO2 - End User'
).mark_line(interpolate= 'cardinal').encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lco2_enduser:Q',
        axis= alt.Axis(
            title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
        )
    ),
    color= alt.Color('E_BESS:Q').scale(scheme= 'reds'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)
points_econ_lco2= alt.Chart(paretos_basecase_econ_e_bess).mark_circle().encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lco2_enduser:Q',
        axis= alt.Axis(
            title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
        )
    ),
    color= alt.Color('E_BESS:Q').scale(scheme= 'reds'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)

lines_env_lco2=  alt.Chart(
    paretos_basecase_env_e_bess,
    title= 'LCO2 - End User'
).mark_line(interpolate= 'cardinal').encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lco2_enduser:Q',
        axis= alt.Axis(
            title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
        )
    ),
    color= alt.Color('E_BESS:Q').scale(scheme= 'greens'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)
points_env_lco2= alt.Chart(paretos_basecase_env_e_bess).mark_circle().encode(
    x= alt.X(
        'ress:Q',
        axis= alt.Axis(
            title= 'Renewable Energy Self-Sufficiency [%]'
        )
    ),
    y= alt.Y(
        'lco2_enduser:Q',
        axis= alt.Axis(
            title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
        )
    ),
    color= alt.Color('E_BESS:Q').scale(scheme= 'greens'),
    tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'T_BESS', 'E_BESS'])
).properties(height= 400, width= 400)





alt.hconcat(
    alt.layer(
        alt.layer(
            lines_econ_lcoe,
            points_econ_lcoe
        ),#.resolve_scale(color= 'independent'),
        alt.layer(
            lines_env_lcoe,
            points_env_lcoe
        )#.resolve_scale(color= 'independent')
    ).resolve_scale(color= 'independent'),
    alt.layer(
        alt.layer(
            lines_econ_lco2,
            points_econ_lco2
        ),#.resolve_scale(color= 'independent'),
        alt.layer(
            lines_env_lco2,
            points_env_lco2
        )#.resolve_scale(color= 'independent')
    ).resolve_scale(color= 'independent'),
)

alt.HConcatChart(...)

___
___


___
___
### BaseCase - SE3 with Residential Load

In [61]:
paretos_basecase_econ= extract_pareto_front_curve(results_econ_sweden_residential4, 'SE3', 'residential4', 'lcoe_investor', 'ress')
paretos_basecase_env= extract_pareto_front_curve(results_env_sweden_residential4, 'SE3', 'residential4', 'lco2_investor', 'ress')

alt.hconcat(
    alt.layer(
        alt.Chart(
            paretos_basecase_econ,
            title= alt.Title(
                'LCOE - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= 'red',
            strokeDash= (0, 0),
            opacity= 1.0
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lcoe_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised Cost Of Energy [EUR/kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
            tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'E_BESS', 'T_BESS'])
        ),
        alt.Chart(
            paretos_basecase_env,
            title= alt.Title(
                'LCOE - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= 'green',
            strokeDash= (5, 5),
            opacity= 0.35
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lcoe_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised Cost Of Energy [EUR/kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
            tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'E_BESS', 'T_BESS'])
        )
    ).properties(height = 500, width=500),
    alt.layer(
        alt.Chart(
            paretos_basecase_econ,
            title= alt.Title(
                'LCO₂eq - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= 'red',
            strokeDash= (0, 0),
            opacity= 0.35
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lco2_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
            tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'E_BESS', 'T_BESS'])
        ),
        alt.Chart(
            paretos_basecase_env,
            title= alt.Title(
                'LCO₂eq - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= 'green',
            strokeDash= (5, 5),
            opacity= 1.0
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lco2_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
            tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'E_BESS', 'T_BESS'])
        )
    ).properties(height = 500, width=500)
)

alt.HConcatChart(...)

In [68]:
alt.hconcat(
    alt.layer(
        alt.Chart(
            paretos_basecase_econ,
            title= alt.Title(
                'LCOE - End User',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= 'red',
            strokeDash= (0, 0),
            opacity= 1.0
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lcoe_enduser:Q',
                axis= alt.Axis(
                    title= 'Levelised Cost Of Energy [EUR/kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
            tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'E_BESS', 'T_BESS'])
        ),
        alt.Chart(
            paretos_basecase_env_clean,
            title= alt.Title(
                'LCOE - End User',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= 'green',
            strokeDash= (5, 5),
            opacity= 0.35
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lcoe_enduser:Q',
                axis= alt.Axis(
                    title= 'Levelised Cost Of Energy [EUR/kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
            tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'E_BESS', 'T_BESS'])
        )
    ).properties(height = 500, width=500),
    alt.layer(
        alt.Chart(
            paretos_basecase_econ,
            title= alt.Title(
                'LCO₂eq - End User',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= 'red',
            strokeDash= (0, 0),
            opacity= 0.35
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lco2_enduser:Q',
                axis= alt.Axis(
                    title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
            tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'E_BESS', 'T_BESS'])
        ),
        alt.Chart(
            paretos_basecase_env_clean,
            title= alt.Title(
                'LCO₂eq - End User',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= 'green',
            strokeDash= (5, 5),
            opacity= 1.0
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lco2_enduser:Q',
                axis= alt.Axis(
                    title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
            tooltip= alt.Tooltip(['P_PV', 'P_BESS', 'E_BESS', 'T_BESS'])
        )
    ).properties(height = 500, width=500)
)

alt.HConcatChart(...)

___
___
### Comparisons #1 - Residential Load with Italy & Poland

In [71]:
paretos_basecase_econ=              extract_pareto_front_curve(results_econ_sweden,     'SE',   'residential4', 'lcoe_investor',    'ress')
paretos_basecase_env=               extract_pareto_front_curve(results_env_sweden,      'SE',   'residential4', 'lco2_investor',    'ress')
paretos_comparisons1_italy_econ=    extract_pareto_front_curve(results_econ_italy,      'IT',   'residential4', 'lcoe_investor',    'ress')
paretos_comparisons1_italy_env=     extract_pareto_front_curve(results_env_italy,       'IT',   'residential4', 'lco2_investor',    'ress')
paretos_comparisons1_poland_econ=   extract_pareto_front_curve(results_econ_poland,     'PL',   'residential4', 'lcoe_investor',    'ress')
paretos_comparisons1_poland_env=    extract_pareto_front_curve(results_env_poland,      'PL',   'residential4', 'lco2_investor',    'ress')
paretos_comparisons1_germany_econ=  extract_pareto_front_curve(results_econ_germany,    'DE',   'residential4', 'lcoe_investor',    'ress')
paretos_comparisons1_germany_env=   extract_pareto_front_curve(results_env_germany,     'DE',   'residential4', 'lco2_investor',    'ress')
paretos_comparisons1_spain_econ=    extract_pareto_front_curve(results_econ_spain,      'ES',   'residential4', 'lcoe_investor',    'ress')
paretos_comparisons1_spain_env=     extract_pareto_front_curve(results_env_spain,       'ES',   'residential4', 'lco2_investor',    'ress')
paretos_comparisons1_se1_econ=      extract_pareto_front_curve(results_econ_se1,        'SE1',  'residential4', 'lcoe_investor',    'ress')
paretos_comparisons1_se1_env=       extract_pareto_front_curve(results_env_se1,         'SE1',  'residential4', 'lco2_investor',    'ress')
paretos_comparisons1_se2_econ=      extract_pareto_front_curve(results_econ_se2,        'SE2',  'residential4', 'lcoe_investor',    'ress')
paretos_comparisons1_se2_env=       extract_pareto_front_curve(results_env_se2,         'SE2',  'residential4', 'lco2_investor',    'ress')
paretos_comparisons1_se3_econ=      extract_pareto_front_curve(results_econ_se3,        'SE3',  'residential4', 'lcoe_investor',    'ress')
paretos_comparisons1_se3_env=       extract_pareto_front_curve(results_env_se3,         'SE3',  'residential4', 'lco2_investor',    'ress')
paretos_comparisons1_se4_econ=      extract_pareto_front_curve(results_econ_se4,        'SE4',  'residential4', 'lcoe_investor',    'ress')
paretos_comparisons1_se4_env=       extract_pareto_front_curve(results_env_se4,         'SE4',  'residential4', 'lco2_investor',    'ress')
paretos_comparisons1_italy_econ=    remove_rows_below_specific_value(paretos_comparisons1_italy_econ,   'ress', 20)
paretos_comparisons1_italy_env=     remove_rows_below_specific_value(paretos_comparisons1_italy_env,    'ress', 20)
paretos_comparisons1_poland_econ=   remove_rows_below_specific_value(paretos_comparisons1_poland_econ,  'ress', 20)
paretos_comparisons1_poland_env=    remove_rows_below_specific_value(paretos_comparisons1_poland_env,   'ress', 20)
paretos_comparisons1_germany_econ=  remove_rows_below_specific_value(paretos_comparisons1_germany_econ, 'ress', 20)
paretos_comparisons1_germany_env=   remove_rows_below_specific_value(paretos_comparisons1_germany_env,  'ress', 20)
paretos_comparisons1_spain_econ=    remove_rows_below_specific_value(paretos_comparisons1_spain_econ,   'ress', 20)
paretos_comparisons1_spain_env=     remove_rows_below_specific_value(paretos_comparisons1_spain_env,    'ress', 20)
paretos_comparisons1_se1_econ=      remove_rows_below_specific_value(paretos_comparisons1_se1_econ,     'ress', 20)
paretos_comparisons1_se1_env=       remove_rows_below_specific_value(paretos_comparisons1_se1_env,      'ress', 20)
paretos_comparisons1_se2_econ=      remove_rows_below_specific_value(paretos_comparisons1_se2_econ,     'ress', 20)
paretos_comparisons1_se2_env=       remove_rows_below_specific_value(paretos_comparisons1_se2_env,      'ress', 20)
paretos_comparisons1_se3_econ=      remove_rows_below_specific_value(paretos_comparisons1_se3_econ,     'ress', 20)
paretos_comparisons1_se3_env=       remove_rows_below_specific_value(paretos_comparisons1_se3_env,      'ress', 20)
paretos_comparisons1_se4_econ=      remove_rows_below_specific_value(paretos_comparisons1_se4_econ,     'ress', 20)
paretos_comparisons1_se4_env=       remove_rows_below_specific_value(paretos_comparisons1_se4_env,      'ress', 20)



alt.hconcat(
    alt.layer(
        alt.Chart(
            paretos_basecase_econ,
            title= alt.Title(
                'LCOE - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= 'blue',
            opacity= 0.6
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lcoe_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised Cost Of Energy [EUR/kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons1_italy_econ,
            title= alt.Title(
                'LCOE - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= '#206b00',
            opacity= 0.6
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lcoe_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised Cost Of Energy [EUR/kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons1_poland_econ,
            title= alt.Title(
                'LCOE - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= 'salmon',
            opacity= 0.6
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lcoe_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised Cost Of Energy [EUR/kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons1_spain_econ,
            title= alt.Title(
                'LCOE - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= 'orange',
            opacity= 0.6
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lcoe_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised Cost Of Energy [EUR/kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons1_germany_econ,
            title= alt.Title(
                'LCOE - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= 'black',
            opacity= 0.6
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lcoe_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised Cost Of Energy [EUR/kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons1_se1_econ,
            title= alt.Title(
                'LCOE - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= 'navy',
            opacity= 0.6
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lcoe_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised Cost Of Energy [EUR/kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons1_se2_econ,
            title= alt.Title(
                'LCOE - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= 'navy',
            opacity= 0.35
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lcoe_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised Cost Of Energy [EUR/kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons1_se3_econ,
            title= alt.Title(
                'LCOE - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= 'lightblue',
            opacity= 0.6
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lcoe_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised Cost Of Energy [EUR/kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons1_se4_econ,
            title= alt.Title(
                'LCOE - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= 'lightblue',
            opacity= 0.35
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lcoe_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised Cost Of Energy [EUR/kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
    ).properties(height = 500, width=500),
    alt.layer(
        alt.layer(
        alt.Chart(
            paretos_basecase_env,
            title= alt.Title(
                'LCO2eq - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= 'blue',
            opacity= 0.6
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lco2_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons1_italy_env,
            title= alt.Title(
                'LCO2eq - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= '#206b00',
            opacity= 0.6
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lco2_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons1_poland_env,
            title= alt.Title(
                'LCO2eq - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= 'salmon',
            opacity= 0.6
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lco2_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons1_spain_env,
            title= alt.Title(
                'LCO2eq - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= 'orange',
            opacity= 0.6
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lco2_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons1_germany_env,
            title= alt.Title(
                'LCO2eq - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= 'black',
            opacity= 0.6
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lco2_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons1_se1_env,
            title= alt.Title(
                'LCO2eq - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= 'navy',
            opacity= 0.6
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lco2_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons1_se2_env,
            title= alt.Title(
                'LCO2eq - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= 'navy',
            opacity= 0.35
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lco2_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons1_se3_env,
            title= alt.Title(
                'LCO2eq - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= 'lightblue',
            opacity= 0.6
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lco2_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons1_se4_env,
            title= alt.Title(
                'LCO2eq - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= 'lightblue',
            opacity= 0.35
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lco2_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
    ).properties(height = 500, width=500),
        # alt.Chart(
        #     paretos_basecase_econ,
        #     title= alt.Title(
        #         'LCO₂eq - Investor',
        #         fontSize= 20
        #     )
        # ).mark_line(
        #     size= 5,
        #     color= 'blue',
        #     opacity= 0.6
        # ).encode(
        #     x= alt.X(
        #         'ress:Q',
        #         axis= alt.Axis(
        #             title= 'Renewable Energy Self-Sufficiency [%]',
        #             titleFontSize= 18,
        #             labelFontSize= 15
        #         )
        #     ).scale(domain= (0, 100)),
        #     y= alt.Y(
        #         'lco2_investor:Q',
        #         axis= alt.Axis(
        #             title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]',
        #             titleFontSize= 18,
        #             labelFontSize= 15
        #         )
        #     ),
        # ),
        # alt.Chart(
        #     paretos_basecase_env,
        #     title= alt.Title(
        #         'LCO₂eq - Investor',
        #         fontSize= 20
        #     )
        # ).mark_line(
        #     size= 5,
        #     color= 'blue',
        #     opacity= 0.6
        # ).encode(
        #     x= alt.X(
        #         'ress:Q',
        #         axis= alt.Axis(
        #             title= 'Renewable Energy Self-Sufficiency [%]',
        #             titleFontSize= 18,
        #             labelFontSize= 15
        #         )
        #     ).scale(domain= (0, 100)),
        #     y= alt.Y(
        #         'lco2_investor:Q',
        #         axis= alt.Axis(
        #             title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]',
        #             titleFontSize= 18,
        #             labelFontSize= 15
        #         )
        #     ),
        # ),
        # alt.Chart(
        #     paretos_comparisons1_italy_econ,
        #     title= alt.Title(
        #         'LCO₂eq - Investor',
        #         fontSize= 20
        #     )
        # ).mark_line(
        #     size= 5,
        #     color= '#206b00',
        #     opacity= 0.6
        # ).encode(
        #     x= alt.X(
        #         'ress:Q',
        #         axis= alt.Axis(
        #             title= 'Renewable Energy Self-Sufficiency [%]',
        #             titleFontSize= 18,
        #             labelFontSize= 15
        #         )
        #     ).scale(domain= (0, 100)),
        #     y= alt.Y(
        #         'lco2_investor:Q',
        #         axis= alt.Axis(
        #             title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]',
        #             titleFontSize= 18,
        #             labelFontSize= 15
        #         )
        #     ),
        # ),
        # alt.Chart(
        #     paretos_comparisons1_italy_env,
        #     title= alt.Title(
        #         'LCO₂eq - Investor',
        #         fontSize= 20
        #     )
        # ).mark_line(
        #     size= 5,
        #     color= '#206b00',
        #     opacity= 0.6
        # ).encode(
        #     x= alt.X(
        #         'ress:Q',
        #         axis= alt.Axis(
        #             title= 'Renewable Energy Self-Sufficiency [%]',
        #             titleFontSize= 18,
        #             labelFontSize= 15
        #         )
        #     ).scale(domain= (0, 100)),
        #     y= alt.Y(
        #         'lco2_investor:Q',
        #         axis= alt.Axis(
        #             title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]',
        #             titleFontSize= 18,
        #             labelFontSize= 15
        #         )
        #     ),
        # ),
        # alt.Chart(
        #     paretos_comparisons1_poland_econ,
        #     title= alt.Title(
        #         'LCO₂eq - Investor',
        #         fontSize= 20
        #     )
        # ).mark_line(
        #     size= 5,
        #     color= 'salmon',
        #     opacity= 0.6
        # ).encode(
        #     x= alt.X(
        #         'ress:Q',
        #         axis= alt.Axis(
        #             title= 'Renewable Energy Self-Sufficiency [%]',
        #             titleFontSize= 18,
        #             labelFontSize= 15
        #         )
        #     ).scale(domain= (0, 100)),
        #     y= alt.Y(
        #         'lco2_investor:Q',
        #         axis= alt.Axis(
        #             title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]',
        #             titleFontSize= 18,
        #             labelFontSize= 15
        #         )
        #     ),
        # ),
        # alt.Chart(
        #     paretos_comparisons1_poland_env,
        #     title= alt.Title(
        #         'LCO₂eq - Investor',
        #         fontSize= 20
        #     )
        # ).mark_line(
        #     size= 5,
        #     color= 'salmon',
        #     opacity= 0.6
        # ).encode(
        #     x= alt.X(
        #         'ress:Q',
        #         axis= alt.Axis(
        #             title= 'Renewable Energy Self-Sufficiency [%]',
        #             titleFontSize= 18,
        #             labelFontSize= 15
        #         )
        #     ).scale(domain= (0, 100)),
        #     y= alt.Y(
        #         'lco2_investor:Q',
        #         axis= alt.Axis(
        #             title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]',
        #             titleFontSize= 18,
        #             labelFontSize= 15
        #         )
        #     ),
        # ),
    ).properties(height = 500, width=500)
)

alt.HConcatChart(...)

In [72]:
alt.hconcat(
    alt.layer(
        alt.Chart(
            paretos_basecase_econ,
            title= alt.Title(
                'LCOE - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= 'blue',
            strokeDash= (0, 0),
            opacity= 1.0
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lcoe_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised Cost Of Energy [EUR/kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_basecase_env,
            title= alt.Title(
                'LCOE - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= 'blue',
            strokeDash= (5, 5),
            opacity= 0.35
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lcoe_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised Cost Of Energy [EUR/kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons1_italy_econ,
            title= alt.Title(
                'LCOE - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= '#206b00',
            strokeDash= (0, 0),
            opacity= 1.0
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lcoe_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised Cost Of Energy [EUR/kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons1_italy_env,
            title= alt.Title(
                'LCOE - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= '#206b00',
            strokeDash= (5, 5),
            opacity= 0.35
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lcoe_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised Cost Of Energy [EUR/kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons1_poland_econ,
            title= alt.Title(
                'LCOE - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= 'salmon',
            strokeDash= (0, 0),
            opacity= 1.0
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lcoe_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised Cost Of Energy [EUR/kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons1_poland_env,
            title= alt.Title(
                'LCOE - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= 'salmon',
            strokeDash= (5, 5),
            opacity= 0.35
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lcoe_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised Cost Of Energy [EUR/kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
    ).properties(height = 500, width=500),
    alt.layer(
        alt.Chart(
            paretos_basecase_econ,
            title= alt.Title(
                'LCO₂eq - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= 'blue',
            strokeDash= (0, 0),
            opacity= 0.35
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lco2_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_basecase_env,
            title= alt.Title(
                'LCO₂eq - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= 'blue',
            strokeDash= (5, 5),
            opacity= 1.0
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lco2_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons1_italy_econ,
            title= alt.Title(
                'LCO₂eq - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= '#206b00',
            strokeDash= (0, 0),
            opacity= 0.35
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lco2_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons1_italy_env,
            title= alt.Title(
                'LCO₂eq - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= '#206b00',
            strokeDash= (5, 5),
            opacity= 1.0
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lco2_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons1_poland_econ,
            title= alt.Title(
                'LCO₂eq - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= 'salmon',
            strokeDash= (0, 0),
            opacity= 0.35
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lco2_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons1_poland_env,
            title= alt.Title(
                'LCO₂eq - Investor',
                fontSize= 20
            )
        ).mark_line(
            size= 5,
            color= 'salmon',
            strokeDash= (5, 5),
            opacity= 1.0
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lco2_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
    ).properties(height = 500, width=500)
)

alt.HConcatChart(...)

___
___
### Comparisons #2 - Industrial Loads #1 & #2 (SE3)

In [ ]:
paretos_basecase_econ=                  extract_pareto_front_curve(results_econ_sweden, 'SE',  'residential4', 'lcoe_investor',    'ress')
paretos_basecase_env=                   extract_pareto_front_curve(results_env_sweden,  'SE',  'residential4', 'lco2_investor',    'ress')
paretos_comparisons2_industrial1_econ=  extract_pareto_front_curve(results_econ_sweden, 'SE',  'industrial1',  'lcoe_investor',    'ress')
paretos_comparisons2_industrial1_env=   extract_pareto_front_curve(results_env_sweden,  'SE',  'industrial1',  'lco2_investor',    'ress')
paretos_comparisons2_industrial2_econ=  extract_pareto_front_curve(results_econ_sweden, 'SE',  'industrial2',  'lcoe_investor',    'ress')
paretos_comparisons2_industrial2_env=   extract_pareto_front_curve(results_env_sweden,  'SE',  'industrial2',  'lco2_investor',    'ress')
paretos_comparisons2_industrial1_econ=  remove_rows_below_specific_value(paretos_comparisons2_industrial1_econ, 'ress', 18)
paretos_comparisons2_industrial1_env=   remove_rows_below_specific_value(paretos_comparisons2_industrial1_env,  'ress', 18)



alt.hconcat(
    alt.layer(
        alt.Chart(
            paretos_basecase_econ,
            title= alt.Title(
                'LCOE - Investor',
                fontSize= 20
            )
        ).mark_line(
            color= 'blue',
            strokeDash= (0, 0),
            opacity= 1.0,
            size= 5
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lcoe_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised Cost Of Energy [EUR/kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_basecase_env,
            title= alt.Title(
                'LCOE - Investor',
                fontSize= 20
            )
        ).mark_line(
            color= 'blue',
            strokeDash= (5, 5),
            opacity= 0.35,
            size= 5
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lcoe_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised Cost Of Energy [EUR/kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons2_industrial1_econ,
            title= alt.Title(
                'LCOE - Investor',
                fontSize= 20
            )
        ).mark_line(
            color= 'orange',
            strokeDash= (0, 0),
            opacity= 1.0,
            size= 5
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lcoe_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised Cost Of Energy [EUR/kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons2_industrial1_env,
            title= alt.Title(
                'LCOE - Investor',
                fontSize= 20
            )
        ).mark_line(
            color= 'orange',
            strokeDash= (5, 5),
            opacity= 0.35,
            size= 5
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lcoe_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised Cost Of Energy [EUR/kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons2_industrial2_econ,
            title= alt.Title(
                'LCOE - Investor',
                fontSize= 20
            )
        ).mark_line(
            color= 'black',
            strokeDash= (0, 0),
            opacity= 1.0,
            size= 5
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lcoe_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised Cost Of Energy [EUR/kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons2_industrial2_env,
            title= alt.Title(
                'LCOE - Investor',
                fontSize= 20
            )
        ).mark_line(
            color= 'black',
            strokeDash= (5, 5),
            opacity= 0.35,
            size= 5
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lcoe_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised Cost Of Energy [EUR/kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
    ).properties(height = 500, width=500),    
    alt.layer(
        alt.Chart(
            paretos_basecase_econ,
            title= alt.Title(
                'LCO₂eq - Investor',
                fontSize= 20
            )
        ).mark_line(
            color= 'blue',
            strokeDash= (0, 0),
            opacity= 0.35,
            size= 5
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lco2_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_basecase_env,
            title= alt.Title(
                'LCO₂eq - Investor',
                fontSize= 20
            )
        ).mark_line(
            color= 'blue',
            strokeDash= (5, 5),
            opacity= 1.0,
            size= 5
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lco2_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons2_industrial1_econ,
            title= alt.Title(
                'LCO₂eq - Investor',
                fontSize= 20
            )
        ).mark_line(
            color= 'orange',
            strokeDash= (0, 0),
            opacity= 0.35,
            size= 5
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lco2_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons2_industrial1_env,
            title= alt.Title(
                'LCO₂eq - Investor',
                fontSize= 20
            )
        ).mark_line(
            color= 'orange',
            strokeDash= (5, 5),
            opacity= 1.0,
            size= 5
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lco2_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons2_industrial2_econ,
            title= alt.Title(
                'LCO₂eq - Investor',
                fontSize= 20
            )
        ).mark_line(
            color= 'black',
            strokeDash= (0, 0),
            opacity= 0.35,
            size= 5
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lco2_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons2_industrial2_env,
            title= alt.Title(
                'LCO₂eq - Investor',
                fontSize= 20
            )
        ).mark_line(
            color= 'black',
            strokeDash= (5, 5),
            opacity= 1.0,
            size= 5
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ).scale(domain= (0, 100)),
            y= alt.Y(
                'lco2_investor:Q',
                axis= alt.Axis(
                    title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]',
                    titleFontSize= 18,
                    labelFontSize= 15
                )
            ),
        ),
    ).properties(height = 500, width=500)
)

In [ ]:
paretos_basecase_econ=                  extract_pareto_front_curve(results_econ_sweden, 'SE',  'residential4', 'lcoe_enduser',    'ress')
paretos_basecase_env=                   extract_pareto_front_curve(results_env_sweden,  'SE',  'residential4', 'lco2_enduser',    'ress')
paretos_comparisons2_industrial1_econ=  extract_pareto_front_curve(results_econ_sweden, 'SE',  'industrial1',  'lcoe_enduser',    'ress')
paretos_comparisons2_industrial1_env=   extract_pareto_front_curve(results_env_sweden,  'SE',  'industrial1',  'lco2_enduser',    'ress')
paretos_comparisons2_industrial2_econ=  extract_pareto_front_curve(results_econ_sweden, 'SE',  'industrial2',  'lcoe_enduser',    'ress')
paretos_comparisons2_industrial2_env=   extract_pareto_front_curve(results_env_sweden,  'SE',  'industrial2',  'lco2_enduser',    'ress')



alt.hconcat(
    alt.layer(
        alt.Chart(
            paretos_basecase_econ,
            title= 'LCOE - End User'
        ).mark_line(
            color= 'blue',
            strokeDash= (0, 0)
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]'
                )
            ),
            y= alt.Y(
                'lcoe_enduser:Q',
                axis= alt.Axis(
                    title= 'Levelised Cost Of Energy [EUR/kWh]'
                )
            ),
        ),
        alt.Chart(
            paretos_basecase_env,
            title= 'LCOE - End User'
        ).mark_line(
            color= 'blue',
            strokeDash= (5, 5)
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]'
                )
            ),
            y= alt.Y(
                'lcoe_enduser:Q',
                axis= alt.Axis(
                    title= 'Levelised Cost Of Energy [EUR/kWh]'
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons2_industrial1_econ,
            title= 'LCOE - End User'
        ).mark_line(
            color= 'orange',
            strokeDash= (0, 0)
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]'
                )
            ),
            y= alt.Y(
                'lcoe_enduser:Q',
                axis= alt.Axis(
                    title= 'Levelised Cost Of Energy [EUR/kWh]'
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons2_industrial1_env,
            title= 'LCOE - End User'
        ).mark_line(
            color= 'orange',
            strokeDash= (5, 5)
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]'
                )
            ),
            y= alt.Y(
                'lcoe_enduser:Q',
                axis= alt.Axis(
                    title= 'Levelised Cost Of Energy [EUR/kWh]'
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons2_industrial2_econ,
            title= 'LCOE - End User'
        ).mark_line(
            color= 'purple',
            strokeDash= (0, 0)
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]'
                )
            ),
            y= alt.Y(
                'lcoe_enduser:Q',
                axis= alt.Axis(
                    title= 'Levelised Cost Of Energy [EUR/kWh]'
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons2_industrial2_env,
            title= 'LCOE - End User'
        ).mark_line(
            color= 'purple',
            strokeDash= (5, 5)
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]'
                )
            ),
            y= alt.Y(
                'lcoe_enduser:Q',
                axis= alt.Axis(
                    title= 'Levelised Cost Of Energy [EUR/kWh]'
                )
            ),
        ),
    ),    
    alt.layer(
        alt.Chart(
            paretos_basecase_econ,
            title= 'LCO₂eq - End User'
        ).mark_line(
            color= 'blue',
            strokeDash= (0, 0)
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]'
                )
            ),
            y= alt.Y(
                'lco2_enduser:Q',
                axis= alt.Axis(
                    title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
                )
            ),
        ),
        alt.Chart(
            paretos_basecase_env,
            title= 'LCO₂eq - End User'
        ).mark_line(
            color= 'blue',
            strokeDash= (5, 5)
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]'
                )
            ),
            y= alt.Y(
                'lco2_enduser:Q',
                axis= alt.Axis(
                    title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons2_industrial1_econ,
            title= 'LCO₂eq - End User'
        ).mark_line(
            color= 'orange',
            strokeDash= (0, 0)
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]'
                )
            ),
            y= alt.Y(
                'lco2_enduser:Q',
                axis= alt.Axis(
                    title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons2_industrial1_env,
            title= 'LCO₂eq - End User'
        ).mark_line(
            color= 'orange',
            strokeDash= (5, 5)
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]'
                )
            ),
            y= alt.Y(
                'lco2_enduser:Q',
                axis= alt.Axis(
                    title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons2_industrial2_econ,
            title= 'LCO₂eq - End User'
        ).mark_line(
            color= 'purple',
            strokeDash= (0, 0)
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]'
                )
            ),
            y= alt.Y(
                'lco2_enduser:Q',
                axis= alt.Axis(
                    title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
                )
            ),
        ),
        alt.Chart(
            paretos_comparisons2_industrial2_env,
            title= 'LCO₂eq - End User'
        ).mark_line(
            color= 'purple',
            strokeDash= (5, 5)
        ).encode(
            x= alt.X(
                'ress:Q',
                axis= alt.Axis(
                    title= 'Renewable Energy Self-Sufficiency [%]'
                )
            ),
            y= alt.Y(
                'lco2_enduser:Q',
                axis= alt.Axis(
                    title= 'Levelised CO₂eq Footprint [gCO₂eq / kWh]'
                )
            ),
        ),
    )
)